In [26]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import random
import os
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor, as_completed

# Function to extract last name for URL
def get_last_name(full_name):
    return full_name.split()[-1].lower()

# Function to scrape player info (with retry logic)
def get_player_info(player_name, player_id, index, total):
    last_name = get_last_name(player_name)
    url = f"https://www.espncricinfo.com/cricketers/{last_name}-{player_id}"

    headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/122.0.0.0 Safari/537.36"
    }

    for attempt in range(3):  # Retry up to 3 times
        try:
            response = requests.get(url, headers=headers, timeout=10)
            if response.status_code == 200:
                break  # Exit loop if request is successful
            print(f"⚠️ Attempt {attempt+1} failed for {player_name}, retrying...")
            time.sleep(random.uniform(2, 5))  # Wait before retrying
        except requests.exceptions.RequestException as e:
            print(f"⚠️ Error: {e} (Retrying {attempt+1}/3)")
            time.sleep(random.uniform(2, 5))
    else:
        print(f"❌ ({index}/{total}) Failed: {url}")
        return {"Player Name": player_name, "Profile URL": url, "Error": "Failed to fetch data"}

    soup = BeautifulSoup(response.text, "html.parser")

    # Extract Full Name
    full_name = "N/A"
    full_name_tag = soup.select_one("div.ds-col-span-2 span p")
    if full_name_tag:
        full_name = full_name_tag.text.strip()

    # Extract Age
    age = "N/A"
    age_tag = soup.select_one("div span p")
    if age_tag:
        age = age_tag.text.strip()

    # Extract Birthdate
    birthdate = "N/A"
    birth_tag = soup.select_one("div p.ds-text-tight-m:-soup-contains('Born') + span p")
    if birth_tag:
        birthdate = birth_tag.text.strip()

    # Extract Profile URL
    profile_url = soup.find("meta", property="og:url")
    profile_url = profile_url["content"] if profile_url else url

    # Extract Image URL
    image_url = "N/A"
    img_tag = soup.select_one("div.ds-bg-cover img")
    if img_tag:
        image_url = img_tag["src"]

    # Extract Country
    country = "N/A"
    country_span = soup.select_one("div.ds-text-raw-white span")
    if country_span:
        country = country_span.text.strip()

    # Extract Major Teams
    major_teams = "N/A"
    team_tags = soup.select("div.ds-grow div:nth-child(2) div > div > div:nth-child(2) > div > a")
    if team_tags:
        major_teams = ", ".join([team.text.strip() for team in team_tags])

    # Extract Batting Style, Bowling Style, Playing Role
    batting_style, bowling_style, playing_role = "N/A", "N/A", "N/A"
    for div in soup.find_all("div"):
        text = div.text.strip()
        if "Batting Style" in text:
            batting_style = text.replace("Batting Style", "").strip()
        elif "Bowling Style" in text:
            bowling_style = text.replace("Bowling Style", "").strip()
        elif "Playing Role" in text:
            playing_role = text.replace("Playing Role", "").strip()

    # Print progress
    print(f"✅ ({index}/{total}) Done: {full_name}")

    return {
        "Player Name": player_name,
        "Full Name": full_name,
        "Age": age,
        "Born": birthdate,
        "Profile URL": profile_url,
        "Country": country,
        "Batting Style": batting_style,
        "Bowling Style": bowling_style,
        "Playing Role": playing_role,
        "Major Teams": major_teams,
        "Image URL": image_url
    }

# Load all players from CSV
df = pd.read_csv(r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\people.csv")
total_players = len(df)

# Directory to save batch files
batch_dir = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\player_batches"
os.makedirs(batch_dir, exist_ok=True)

# Save progress every 50 players
batch_size = 50  
players_data = []
output_file = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\players meta data.csv"

# Define the number of threads (parallel requests)
num_threads = 5  # Adjust this for performance

# Function to process players in batches
def process_batch(batch, batch_num):
    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        futures = {executor.submit(get_player_info, row["unique_name"], str(row["key_cricinfo"]), i + 1, total_players): row for i, row in batch.iterrows()}
        results = [future.result() for future in tqdm(as_completed(futures), total=len(futures), desc=f"Batch {batch_num}")]

    return results

# Process players in parallel batches
for batch_num, batch_start in enumerate(range(0, total_players, batch_size), start=1):
    batch = df.iloc[batch_start:batch_start + batch_size]
    batch_results = process_batch(batch, batch_num)

    # Save batch file
    batch_filename = os.path.join(batch_dir, f"scraped_batch_{batch_num}.csv")
    df_batch = pd.DataFrame(batch_results)
    df_batch.to_csv(batch_filename, index=False)
    df_batch.to_csv(output_file, mode="a", header=not os.path.exists(output_file), index=False)

    print(f"💾 Saved: {batch_filename} & Progress saved in main file.")

print("\n✅ Full scraping complete! 🎯 Saved as 'scraped_all_players.csv'")

In [20]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2"

# Required columns from the info file
required_columns = [
    "gender", "event", "match_number", "toss_winner",
    "toss_decision", "player_of_match", "winner", "winner_runs", "winner_wickets", "outcome"
]

# Function to process info file
def process_info_file(info_file):
    with open(info_file, "r", encoding="utf-8") as f:
        lines = f.readlines()

    # Split each line into max 3 parts: Category, Attribute, and Value
    structured_data = []
    for line in lines:
        parts = line.strip().split(",", 2)  # Split into max 3 parts
        if len(parts) == 2:  
            parts.append("")  # Ensure we always have 3 columns
        structured_data.append(parts)

    # Convert to DataFrame
    df_info = pd.DataFrame(structured_data, columns=["Category", "Attribute", "Value"])

    # Remove extra spaces and quotes
    df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)

    # Extract required attributes
    df_filtered = df_info[df_info["Attribute"].isin(required_columns)][["Attribute", "Value"]]

    # Convert to a single-row DataFrame with attributes as columns
    df_final = df_filtered.set_index("Attribute").T.reset_index(drop=True)

    return df_final

# Function to process match file
def process_match_file(match_file):
    df = pd.read_csv(match_file)

    # Add Wicket column
    df["Wicket"] = df["player_dismissed"].notna().astype(int)

    # Initialize dictionaries to track stats
    balls_faced = {}
    total_runs = {}
    player_out_runs = {}
    player_out_balls = {}

    # Process the dataset
    for i, row in df.iterrows():
        striker = row["striker"]
        player_out = row["player_dismissed"]

        # Update balls faced by striker
        balls_faced[striker] = balls_faced.get(striker, 0) + 1

        # Update total runs scored by striker
        total_runs[striker] = total_runs.get(striker, 0) + row["runs_off_bat"]

        # If a player is out, record their runs and balls faced
        if pd.notna(player_out):
            player_out_runs[player_out] = total_runs.get(player_out, 0)
            player_out_balls[player_out] = balls_faced.get(player_out, 0)

        # Assign values to new columns
        df.at[i, "Striker Balls Faced"] = balls_faced[striker]
        df.at[i, "Total Striker Runs"] = total_runs[striker]
        df.at[i, "Player Out Runs"] = player_out_runs.get(player_out, None)
        df.at[i, "Player Out Balls Faced"] = player_out_balls.get(player_out, None)

    # Fill NaN values with 0 for consistency
    #df.fillna(0, inplace=True)

    return df

# Get all match CSV files (excluding info files)
files = [f for f in os.listdir(folder) if f.endswith(".csv") and "_info.csv" not in f]

# Process each match file
for file in files:
    match_file = os.path.join(folder, file)
    info_file = os.path.join(folder, file.replace(".csv", "_info.csv"))

    if os.path.exists(info_file):  # Ensure the info file exists
        # Read ball-by-ball data
        df_match = process_match_file(match_file)

        # Process the info file
        df_info_filtered = process_info_file(info_file)

        # Ensure all required columns exist
        for col in required_columns:
            if col not in df_info_filtered.columns:
                df_info_filtered[col] = None  # Add missing columns with NaN

        # Repeat the info row for all match rows
        df_info_expanded = pd.concat([df_info_filtered] * len(df_match), ignore_index=True)

        # Concatenate with match data
        df_combined = pd.concat([df_match, df_info_expanded], axis=1)

        # Save the merged CSV
        output_file = os.path.join(folder, file.replace(".csv", "_combined.csv"))
        df_combined.to_csv(output_file, index=False)

        print(f"Processed and saved: {output_file}")

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2048260422.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2\1000851_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2048260422.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2\1000853_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2048260422.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


...

Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2\995451_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2048260422.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2\995453_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2048260422.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2\995455_combined.csv


In [21]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\tests_csv2"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_combined.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    
    # Add the "format" column with "TEST" as the value
    df["format"] = "TEST"
    df["type"] = "Intl"
    dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)

df_match = final_df
player_metadata_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\players meta data.csv"

df_metadata = pd.read_csv(player_metadata_path)

# Standardizing column names (removing extra spaces)
df_metadata.rename(columns=lambda x: x.strip(), inplace=True)

# Define metadata columns to be merged
metadata_cols = ["Full Name", "Country", 
                 "Batting Style", "Bowling Style", "Playing Role", 
                 "Major Teams", "Image URL"]

# Function to merge player metadata with proper suffix
def merge_player_metadata(df, player_role):
    # Preserve original column values
    original_col = df[player_role].copy()

    # Merge metadata
    merged_df = df.merge(df_metadata, left_on=player_role, right_on="Player Name", how="left")

    # Rename metadata columns with a suffix
    rename_mapping = {col: f"{col}_{player_role}" for col in metadata_cols}
    merged_df.rename(columns=rename_mapping, inplace=True)

    # Restore original player_role column (overwrites if any merge messed it up)
    merged_df[player_role] = original_col

    # Drop unnecessary columns
    columns_to_drop = [col for col in merged_df.columns if col.endswith("_x") or col.endswith("_y") or col in ["Age", "Born", "Profile URL", "Error"]]
    merged_df.drop(columns=columns_to_drop, inplace=True, errors="ignore")

    merged_df.drop(columns=["Player Name"], inplace=True, errors="ignore")

    return merged_df


# Merge metadata for striker, non-striker, and bowler
df_merged = merge_player_metadata(df_match, "striker")
df_merged = merge_player_metadata(df_merged, "bowler")

# Save the final merged dataset
output_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\test_merged_data.csv"
df_merged.to_csv(output_path, index=False)

print(f"Merged dataset saved successfully at: {output_path}")

Merged dataset saved successfully at: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\test_merged_data.csv


In [23]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2"

# Required columns from the info file
required_columns = [
    "gender", "event", "match_number", "toss_winner",
    "toss_decision", "player_of_match", "winner", "winner_runs", "winner_wickets", "outcome"
]

# Function to process info file
def process_info_file(info_file):
    with open(info_file, "r", encoding="utf-8") as f:
        lines = f.readlines()

    # Split each line into max 3 parts: Category, Attribute, and Value
    structured_data = []
    for line in lines:
        parts = line.strip().split(",", 2)  # Split into max 3 parts
        if len(parts) == 2:  
            parts.append("")  # Ensure we always have 3 columns
        structured_data.append(parts)

    # Convert to DataFrame
    df_info = pd.DataFrame(structured_data, columns=["Category", "Attribute", "Value"])

    # Remove extra spaces and quotes
    df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)

    # Extract required attributes
    df_filtered = df_info[df_info["Attribute"].isin(required_columns)][["Attribute", "Value"]]

    # Convert to a single-row DataFrame with attributes as columns
    df_final = df_filtered.set_index("Attribute").T.reset_index(drop=True)

    return df_final

# Function to process match file
def process_match_file(match_file):
    df = pd.read_csv(match_file)

    # Add Wicket column
    df["Wicket"] = df["player_dismissed"].notna().astype(int)

    # Initialize dictionaries to track stats
    balls_faced = {}
    total_runs = {}
    player_out_runs = {}
    player_out_balls = {}

    # Process the dataset
    for i, row in df.iterrows():
        striker = row["striker"]
        player_out = row["player_dismissed"]

        # Update balls faced by striker
        balls_faced[striker] = balls_faced.get(striker, 0) + 1

        # Update total runs scored by striker
        total_runs[striker] = total_runs.get(striker, 0) + row["runs_off_bat"]

        # If a player is out, record their runs and balls faced
        if pd.notna(player_out):
            player_out_runs[player_out] = total_runs.get(player_out, 0)
            player_out_balls[player_out] = balls_faced.get(player_out, 0)

        # Assign values to new columns
        df.at[i, "Striker Balls Faced"] = balls_faced[striker]
        df.at[i, "Total Striker Runs"] = total_runs[striker]
        df.at[i, "Player Out Runs"] = player_out_runs.get(player_out, None)
        df.at[i, "Player Out Balls Faced"] = player_out_balls.get(player_out, None)

    # Fill NaN values with 0 for consistency
    #df.fillna(0, inplace=True)

    return df

# Get all match CSV files (excluding info files)
files = [f for f in os.listdir(folder) if f.endswith(".csv") and "_info.csv" not in f]

# Process each match file
for file in files:
    match_file = os.path.join(folder, file)
    info_file = os.path.join(folder, file.replace(".csv", "_info.csv"))

    if os.path.exists(info_file):  # Ensure the info file exists
        # Read ball-by-ball data
        df_match = process_match_file(match_file)

        # Process the info file
        df_info_filtered = process_info_file(info_file)

        # Ensure all required columns exist
        for col in required_columns:
            if col not in df_info_filtered.columns:
                df_info_filtered[col] = None  # Add missing columns with NaN

        # Repeat the info row for all match rows
        df_info_expanded = pd.concat([df_info_filtered] * len(df_match), ignore_index=True)

        # Concatenate with match data
        df_combined = pd.concat([df_match, df_info_expanded], axis=1)

        # Save the merged CSV
        output_file = os.path.join(folder, file.replace(".csv", "_combined.csv"))
        df_combined.to_csv(output_file, index=False)

        print(f"Processed and saved: {output_file}")

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\1000887_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\1000889_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


...

Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\995461_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\995463_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\995465_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3784463059.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\997993_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2\997995_combined.csv


In [24]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odis_csv2"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_combined.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    
    # Add the "format" column with "TEST" as the value
    df["format"] = "ODI"
    df["type"] = "Intl"
    dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)

df_match = final_df
player_metadata_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\players meta data.csv"

df_metadata = pd.read_csv(player_metadata_path)

# Standardizing column names (removing extra spaces)
df_metadata.rename(columns=lambda x: x.strip(), inplace=True)

# Define metadata columns to be merged
metadata_cols = ["Full Name", "Country", 
                 "Batting Style", "Bowling Style", "Playing Role", 
                 "Major Teams", "Image URL"]

# Function to merge player metadata with proper suffix
def merge_player_metadata(df, player_role):
    # Preserve original column values
    original_col = df[player_role].copy()

    # Merge metadata
    merged_df = df.merge(df_metadata, left_on=player_role, right_on="Player Name", how="left")

    # Rename metadata columns with a suffix
    rename_mapping = {col: f"{col}_{player_role}" for col in metadata_cols}
    merged_df.rename(columns=rename_mapping, inplace=True)

    # Restore original player_role column (overwrites if any merge messed it up)
    merged_df[player_role] = original_col

    # Drop unnecessary columns
    columns_to_drop = [col for col in merged_df.columns if col.endswith("_x") or col.endswith("_y") or col in ["Age", "Born", "Profile URL", "Error"]]
    merged_df.drop(columns=columns_to_drop, inplace=True, errors="ignore")

    merged_df.drop(columns=["Player Name"], inplace=True, errors="ignore")

    return merged_df

# Merge metadata for striker, non-striker, and bowler
df_merged = merge_player_metadata(df_match, "striker")
df_merged = merge_player_metadata(df_merged, "bowler")

# Save the final merged dataset
output_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odi_merged_data.csv"
df_merged.to_csv(output_path, index=False)

print(f"Merged dataset saved successfully at: {output_path}")

Merged dataset saved successfully at: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\odi_merged_data.csv


In [29]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2"

# Required columns from the info file
required_columns = [
    "gender", "event", "match_number", "toss_winner",
    "toss_decision", "player_of_match", "winner", "winner_runs", "winner_wickets", "outcome"
]

# Function to process info file
def process_info_file(info_file):
    with open(info_file, "r", encoding="utf-8") as f:
        lines = f.readlines()

    # Split each line into max 3 parts: Category, Attribute, and Value
    structured_data = []
    for line in lines:
        parts = line.strip().split(",", 2)  # Split into max 3 parts
        if len(parts) == 2:  
            parts.append("")  # Ensure we always have 3 columns
        structured_data.append(parts)

    # Convert to DataFrame
    df_info = pd.DataFrame(structured_data, columns=["Category", "Attribute", "Value"])

    # Remove extra spaces and quotes
    df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)

    # Extract required attributes
    df_filtered = df_info[df_info["Attribute"].isin(required_columns)][["Attribute", "Value"]]

    # Convert to a single-row DataFrame with attributes as columns
    df_final = df_filtered.set_index("Attribute").T.reset_index(drop=True)

    return df_final

# Function to process match file
def process_match_file(match_file):
    df = pd.read_csv(match_file)

    # Add Wicket column
    df["Wicket"] = df["player_dismissed"].notna().astype(int)

    # Initialize dictionaries to track stats
    balls_faced = {}
    total_runs = {}
    player_out_runs = {}
    player_out_balls = {}

    # Process the dataset
    for i, row in df.iterrows():
        striker = row["striker"]
        player_out = row["player_dismissed"]

        # Update balls faced by striker
        balls_faced[striker] = balls_faced.get(striker, 0) + 1

        # Update total runs scored by striker
        total_runs[striker] = total_runs.get(striker, 0) + row["runs_off_bat"]

        # If a player is out, record their runs and balls faced
        if pd.notna(player_out):
            player_out_runs[player_out] = total_runs.get(player_out, 0)
            player_out_balls[player_out] = balls_faced.get(player_out, 0)

        # Assign values to new columns
        df.at[i, "Striker Balls Faced"] = balls_faced[striker]
        df.at[i, "Total Striker Runs"] = total_runs[striker]
        df.at[i, "Player Out Runs"] = player_out_runs.get(player_out, None)
        df.at[i, "Player Out Balls Faced"] = player_out_balls.get(player_out, None)

    # Fill NaN values with 0 for consistency
    #df.fillna(0, inplace=True)

    return df

# Get all match CSV files (excluding info files)
files = [f for f in os.listdir(folder) if f.endswith(".csv") and "_info.csv" not in f]

# Process each match file
for file in files:
    match_file = os.path.join(folder, file)
    info_file = os.path.join(folder, file.replace(".csv", "_info.csv"))

    if os.path.exists(info_file):  # Ensure the info file exists
        # Read ball-by-ball data
        df_match = process_match_file(match_file)

        # Process the info file
        df_info_filtered = process_info_file(info_file)

        # Ensure all required columns exist
        for col in required_columns:
            if col not in df_info_filtered.columns:
                df_info_filtered[col] = None  # Add missing columns with NaN

        # Repeat the info row for all match rows
        df_info_expanded = pd.concat([df_info_filtered] * len(df_match), ignore_index=True)

        # Concatenate with match data
        df_combined = pd.concat([df_match, df_info_expanded], axis=1)

        # Save the merged CSV
        output_file = os.path.join(folder, file.replace(".csv", "_combined.csv"))
        df_combined.to_csv(output_file, index=False)

        print(f"Processed and saved: {output_file}")

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1001349_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1001351_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1001353_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1004729_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1007655_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1007657_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1007659_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\1019979_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


...

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppDa

Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966753_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966755_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966757_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966759_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966761_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppDa

Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966763_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\966765_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\967081_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\995467_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2\995469_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\702037263.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


In [30]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20s_csv2"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_combined.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    
    # Add the "format" column with "TEST" as the value
    df["format"] = "T20"
    df["type"] = "Intl"
    
    dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)

df_match = final_df
player_metadata_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\players meta data.csv"

df_metadata = pd.read_csv(player_metadata_path)

# Standardizing column names (removing extra spaces)
df_metadata.rename(columns=lambda x: x.strip(), inplace=True)

# Define metadata columns to be merged
metadata_cols = ["Full Name", "Country", 
                 "Batting Style", "Bowling Style", "Playing Role", 
                 "Major Teams", "Image URL"]

# Function to merge player metadata with proper suffix
def merge_player_metadata(df, player_role):
    # Preserve original column values
    original_col = df[player_role].copy()

    # Merge metadata
    merged_df = df.merge(df_metadata, left_on=player_role, right_on="Player Name", how="left")

    # Rename metadata columns with a suffix
    rename_mapping = {col: f"{col}_{player_role}" for col in metadata_cols}
    merged_df.rename(columns=rename_mapping, inplace=True)

    # Restore original player_role column (overwrites if any merge messed it up)
    merged_df[player_role] = original_col

    # Drop unnecessary columns
    columns_to_drop = [col for col in merged_df.columns if col.endswith("_x") or col.endswith("_y") or col in ["Age", "Born", "Profile URL", "Error"]]
    merged_df.drop(columns=columns_to_drop, inplace=True, errors="ignore")

    merged_df.drop(columns=["Player Name"], inplace=True, errors="ignore")

    return merged_df

# Merge metadata for striker, non-striker, and bowler
df_merged = merge_player_metadata(df_match, "striker")
df_merged = merge_player_metadata(df_merged, "bowler")

# Save the final merged dataset
output_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20_merged_data.csv"
df_merged.to_csv(output_path, index=False)

print(f"Merged dataset saved successfully at: {output_path}")

Merged dataset saved successfully at: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\t20_merged_data.csv


In [25]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2"

# Required columns from the info file
required_columns = [
    "gender", "event", "match_number", "toss_winner",
    "toss_decision", "player_of_match", "winner", "winner_runs", "winner_wickets", "outcome"
]

# Function to process info file
def process_info_file(info_file):
    with open(info_file, "r", encoding="utf-8") as f:
        lines = f.readlines()

    # Split each line into max 3 parts: Category, Attribute, and Value
    structured_data = []
    for line in lines:
        parts = line.strip().split(",", 2)  # Split into max 3 parts
        if len(parts) == 2:  
            parts.append("")  # Ensure we always have 3 columns
        structured_data.append(parts)

    # Convert to DataFrame
    df_info = pd.DataFrame(structured_data, columns=["Category", "Attribute", "Value"])

    # Remove extra spaces and quotes
    df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)

    # Extract required attributes
    df_filtered = df_info[df_info["Attribute"].isin(required_columns)][["Attribute", "Value"]]

    # Convert to a single-row DataFrame with attributes as columns
    df_final = df_filtered.set_index("Attribute").T.reset_index(drop=True)

    return df_final

# Function to process match file
def process_match_file(match_file):
    df = pd.read_csv(match_file)

    # Add Wicket column
    df["Wicket"] = df["player_dismissed"].notna().astype(int)

    # Initialize dictionaries to track stats
    balls_faced = {}
    total_runs = {}
    player_out_runs = {}
    player_out_balls = {}

    # Process the dataset
    for i, row in df.iterrows():
        striker = row["striker"]
        player_out = row["player_dismissed"]

        # Update balls faced by striker
        balls_faced[striker] = balls_faced.get(striker, 0) + 1

        # Update total runs scored by striker
        total_runs[striker] = total_runs.get(striker, 0) + row["runs_off_bat"]

        # If a player is out, record their runs and balls faced
        if pd.notna(player_out):
            player_out_runs[player_out] = total_runs.get(player_out, 0)
            player_out_balls[player_out] = balls_faced.get(player_out, 0)

        # Assign values to new columns
        df.at[i, "Striker Balls Faced"] = balls_faced[striker]
        df.at[i, "Total Striker Runs"] = total_runs[striker]
        df.at[i, "Player Out Runs"] = player_out_runs.get(player_out, None)
        df.at[i, "Player Out Balls Faced"] = player_out_balls.get(player_out, None)

    # Fill NaN values with 0 for consistency
    #df.fillna(0, inplace=True)

    return df

# Get all match CSV files (excluding info files)
files = [f for f in os.listdir(folder) if f.endswith(".csv") and "_info.csv" not in f]

# Process each match file
for file in files:
    match_file = os.path.join(folder, file)
    info_file = os.path.join(folder, file.replace(".csv", "_info.csv"))

    if os.path.exists(info_file):  # Ensure the info file exists
        # Read ball-by-ball data
        df_match = process_match_file(match_file)

        # Process the info file
        df_info_filtered = process_info_file(info_file)

        # Ensure all required columns exist
        for col in required_columns:
            if col not in df_info_filtered.columns:
                df_info_filtered[col] = None  # Add missing columns with NaN

        # Repeat the info row for all match rows
        df_info_expanded = pd.concat([df_info_filtered] * len(df_match), ignore_index=True)

        # Concatenate with match data
        df_combined = pd.concat([df_match, df_info_expanded], axis=1)

        # Save the merged CSV
        output_file = os.path.join(folder, file.replace(".csv", "_combined.csv"))
        df_combined.to_csv(output_file, index=False)

        print(f"Processed and saved: {output_file}")

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\1082591_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\1082592_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


...

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\L

Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\980997_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\980999_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981001_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981003_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981005_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981007_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981009_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International 

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981013_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981015_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981017_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2\981019_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\65921925.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


In [26]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_csv2"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_combined.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    
    # Add the "format" column with "TEST" as the value
    df["format"] = "T20"
    df["type"] = "Fran(IPL)"
    
    dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)

df_match = final_df
player_metadata_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\players meta data.csv"

df_metadata = pd.read_csv(player_metadata_path)

# Standardizing column names (removing extra spaces)
df_metadata.rename(columns=lambda x: x.strip(), inplace=True)

# Define metadata columns to be merged
metadata_cols = ["Full Name", "Country", 
                 "Batting Style", "Bowling Style", "Playing Role", 
                 "Major Teams", "Image URL"]

# Function to merge player metadata with proper suffix
def merge_player_metadata(df, player_role):
    # Preserve original column values
    original_col = df[player_role].copy()

    # Merge metadata
    merged_df = df.merge(df_metadata, left_on=player_role, right_on="Player Name", how="left")

    # Rename metadata columns with a suffix
    rename_mapping = {col: f"{col}_{player_role}" for col in metadata_cols}
    merged_df.rename(columns=rename_mapping, inplace=True)

    # Restore original player_role column (overwrites if any merge messed it up)
    merged_df[player_role] = original_col

    # Drop unnecessary columns
    columns_to_drop = [col for col in merged_df.columns if col.endswith("_x") or col.endswith("_y") or col in ["Age", "Born", "Profile URL", "Error"]]
    merged_df.drop(columns=columns_to_drop, inplace=True, errors="ignore")

    merged_df.drop(columns=["Player Name"], inplace=True, errors="ignore")

    return merged_df

# Merge metadata for striker, non-striker, and bowler
df_merged = merge_player_metadata(df_match, "striker")
df_merged = merge_player_metadata(df_merged, "bowler")

# Save the final merged dataset
output_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_merged_data.csv"
df_merged.to_csv(output_path, index=False)

print(f"Merged dataset saved successfully at: {output_path}")

Merged dataset saved successfully at: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\ipl_merged_data.csv


In [27]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2"

# Required columns from the info file
required_columns = [
    "gender", "event", "match_number", "toss_winner",
    "toss_decision", "player_of_match", "winner", "winner_runs", "winner_wickets", "outcome"
]

# Function to process info file
def process_info_file(info_file):
    with open(info_file, "r", encoding="utf-8") as f:
        lines = f.readlines()

    # Split each line into max 3 parts: Category, Attribute, and Value
    structured_data = []
    for line in lines:
        parts = line.strip().split(",", 2)  # Split into max 3 parts
        if len(parts) == 2:  
            parts.append("")  # Ensure we always have 3 columns
        structured_data.append(parts)

    # Convert to DataFrame
    df_info = pd.DataFrame(structured_data, columns=["Category", "Attribute", "Value"])

    # Remove extra spaces and quotes
    df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)

    # Extract required attributes
    df_filtered = df_info[df_info["Attribute"].isin(required_columns)][["Attribute", "Value"]]

    # Convert to a single-row DataFrame with attributes as columns
    df_final = df_filtered.set_index("Attribute").T.reset_index(drop=True)

    return df_final

# Function to process match file
def process_match_file(match_file):
    df = pd.read_csv(match_file)

    # Add Wicket column
    df["Wicket"] = df["player_dismissed"].notna().astype(int)

    # Initialize dictionaries to track stats
    balls_faced = {}
    total_runs = {}
    player_out_runs = {}
    player_out_balls = {}

    # Process the dataset
    for i, row in df.iterrows():
        striker = row["striker"]
        player_out = row["player_dismissed"]

        # Update balls faced by striker
        balls_faced[striker] = balls_faced.get(striker, 0) + 1

        # Update total runs scored by striker
        total_runs[striker] = total_runs.get(striker, 0) + row["runs_off_bat"]

        # If a player is out, record their runs and balls faced
        if pd.notna(player_out):
            player_out_runs[player_out] = total_runs.get(player_out, 0)
            player_out_balls[player_out] = balls_faced.get(player_out, 0)

        # Assign values to new columns
        df.at[i, "Striker Balls Faced"] = balls_faced[striker]
        df.at[i, "Total Striker Runs"] = total_runs[striker]
        df.at[i, "Player Out Runs"] = player_out_runs.get(player_out, None)
        df.at[i, "Player Out Balls Faced"] = player_out_balls.get(player_out, None)

    # Fill NaN values with 0 for consistency
    #df.fillna(0, inplace=True)

    return df

# Get all match CSV files (excluding info files)
files = [f for f in os.listdir(folder) if f.endswith(".csv") and "_info.csv" not in f]

# Process each match file
for file in files:
    match_file = os.path.join(folder, file)
    info_file = os.path.join(folder, file.replace(".csv", "_info.csv"))

    if os.path.exists(info_file):  # Ensure the info file exists
        # Read ball-by-ball data
        df_match = process_match_file(match_file)

        # Process the info file
        df_info_filtered = process_info_file(info_file)

        # Ensure all required columns exist
        for col in required_columns:
            if col not in df_info_filtered.columns:
                df_info_filtered[col] = None  # Add missing columns with NaN

        # Repeat the info row for all match rows
        df_info_expanded = pd.concat([df_info_filtered] * len(df_match), ignore_index=True)

        # Concatenate with match data
        df_combined = pd.concat([df_match, df_info_expanded], axis=1)

        # Save the merged CSV
        output_file = os.path.join(folder, file.replace(".csv", "_combined.csv"))
        df_combined.to_csv(output_file, index=False)

        print(f"Processed and saved: {output_file}")

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358929_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358930_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358931_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358932_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\A

Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358933_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358934_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358935_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358936_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358937_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358938_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1358939_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\Interna

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


...

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469312_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469313_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469314_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469315_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469316_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469317_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469318_combined.csv
Processed and saved: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2\1469319_combined.csv


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\3563063562.py:30: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_info = df_info.applymap(lambda x: x.strip().replace('"', '') if isinstance(x, str) else x)


In [28]:
import os
import pandas as pd

# Folder path
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_csv2"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_combined.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    
    # Add the "format" column with "TEST" as the value
    df["format"] = "T20"
    df["type"] = "Fran(WPL)"
    
    dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)

df_match = final_df
player_metadata_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\players meta data.csv"

df_metadata = pd.read_csv(player_metadata_path)

# Standardizing column names (removing extra spaces)
df_metadata.rename(columns=lambda x: x.strip(), inplace=True)

# Define metadata columns to be merged
metadata_cols = ["Full Name", "Country", 
                 "Batting Style", "Bowling Style", "Playing Role", 
                 "Major Teams", "Image URL"]

# Function to merge player metadata with proper suffix
def merge_player_metadata(df, player_role):
    # Preserve original column values
    original_col = df[player_role].copy()

    # Merge metadata
    merged_df = df.merge(df_metadata, left_on=player_role, right_on="Player Name", how="left")

    # Rename metadata columns with a suffix
    rename_mapping = {col: f"{col}_{player_role}" for col in metadata_cols}
    merged_df.rename(columns=rename_mapping, inplace=True)

    # Restore original player_role column (overwrites if any merge messed it up)
    merged_df[player_role] = original_col

    # Drop unnecessary columns
    columns_to_drop = [col for col in merged_df.columns if col.endswith("_x") or col.endswith("_y") or col in ["Age", "Born", "Profile URL", "Error"]]
    merged_df.drop(columns=columns_to_drop, inplace=True, errors="ignore")

    merged_df.drop(columns=["Player Name"], inplace=True, errors="ignore")

    return merged_df

# Merge metadata for striker, non-striker, and bowler
df_merged = merge_player_metadata(df_match, "striker")
df_merged = merge_player_metadata(df_merged, "bowler")

# Save the final merged dataset
output_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_merged_data.csv"
df_merged.to_csv(output_path, index=False)

print(f"Merged dataset saved successfully at: {output_path}")

Merged dataset saved successfully at: C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\wpl_merged_data.csv


In [32]:
folder = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_merged_data.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)
output_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\final_all_merged_data.csv"
final_df.to_csv(output_path, index=False)

C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2228203767.py:12: DtypeWarning: Columns (1,36) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2228203767.py:12: DtypeWarning: Columns (1,20,21,36,39) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2228203767.py:12: DtypeWarning: Columns (1,20,21,36,39) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)
C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\2228203767.py:12: DtypeWarning: Columns (1,20,21,36,39) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path)


In [33]:
player_metadata_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\final_all_merged_data.csv"

df_metadata = pd.read_csv(player_metadata_path)
df_metadata.info()
# Count total null values per column
null_counts = df_metadata.isnull().sum()

# Display columns with missing values
null_counts = null_counts[null_counts > 0]

print("Columns with missing values:\n", null_counts)


C:\Users\ariad\AppData\Local\Temp\ipykernel_15136\71786687.py:3: DtypeWarning: Columns (1,20,21,36,53) have mixed types. Specify dtype option on import or set low_memory=False.
  df_metadata = pd.read_csv(player_metadata_path)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4431800 entries, 0 to 4431799
Data columns (total 54 columns):
 #   Column                  Dtype  
---  ------                  -----  
 0   match_id                int64  
 1   season                  object 
 2   start_date              object 
 3   venue                   object 
 4   innings                 int64  
 5   ball                    float64
 6   batting_team            object 
 7   bowling_team            object 
 8   striker                 object 
 9   non_striker             object 
 10  bowler                  object 
 11  runs_off_bat            int64  
 12  extras                  int64  
 13  wides                   float64
 14  noballs                 float64
 15  byes                    float64
 16  legbyes                 float64
 17  penalty                 float64
 18  wicket_type             object 
 19  player_dismissed        object 
 20  other_wicket_type       object 
 21  other_player_dismissed  object 

In [3]:
import os
import re

# Folder containing all the HTML files
folder_path = r"C:\Users\ariad\Downloads\Cricket"

# Regex pattern to match full URLs to match-schedule-fixtures
pattern = r"https://www\.espncricinfo\.com/series/[^\s\"'>]+?/match-schedule-fixtures"

# Output file to store the unique links
output_file = os.path.join(folder_path, "schedule_fixtures_links.txt")
all_matches = set()

# Loop through all HTML files in the folder
for filename in os.listdir(folder_path):
    if filename.endswith(".html"):
        file_path = os.path.join(folder_path, filename)
        with open(file_path, "r", encoding="utf-8") as file:
            content = file.read()
            matches = re.findall(pattern, content)
            all_matches.update(matches)

# Sort and save the unique matches
sorted_matches = sorted(all_matches)
with open(output_file, "w", encoding="utf-8") as f:
    f.write("\n".join(sorted_matches))

print(f"✅ Found and saved {len(sorted_matches)} schedule fixture link(s) to:\n{output_file}")

✅ Found and saved 10759 schedule fixture link(s) to:
C:\Users\ariad\Downloads\Cricket\schedule_fixtures_links.txt


In [8]:
import os
import requests
import wget
import logging
import subprocess
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from bs4 import BeautifulSoup
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry
from urllib.parse import urlparse
import time
from time import perf_counter
from tqdm import tqdm

# =============================================================================
# Logging Configuration
# =============================================================================
logging.basicConfig(filename='web_scraper.log', level=logging.INFO,
                    format='%(asctime)s - %(levelname)s - %(message)s')
console = logging.StreamHandler()
console.setLevel(logging.INFO)  # Adjusted to reduce verbosity in the console
formatter = logging.Formatter('%(asctime)s - %(levelname)s - %(message)s')
console.setFormatter(formatter)
logging.getLogger('').addHandler(console)

# =============================================================================
# Persistent Session with Retry Logic
# =============================================================================
session = requests.Session()
retries = Retry(total=3, backoff_factor=0.3, status_forcelist=[500, 502, 503, 504])
adapter = HTTPAdapter(max_retries=retries)
session.mount('http://', adapter)
session.mount('https://', adapter)

# =============================================================================
# Selenium Setup
# =============================================================================
def get_selenium_driver():
    options = Options()
    options.headless = True
    options.add_argument("--disable-gpu")
    options.add_argument("--no-sandbox")
    options.add_argument("--disable-dev-shm-usage")
    driver = webdriver.Chrome(options=options)
    return driver

# =============================================================================
# Utility Functions
# =============================================================================
def save_file(url, destination):
    try:
        logging.debug(f"Downloading file: {url} to {destination}")  # Changed to debug level
        wget.download(url, destination)
        logging.info(f"Successfully downloaded file: {url}")
    except Exception as e:
        logging.error(f"Error downloading file {url}: {e}")

def create_directory(path):
    if not os.path.exists(path):
        os.makedirs(path)
        logging.debug(f"Created directory: {path}")  # Changed to debug level

def read_urls_from_file(file_path):
    with open(file_path, 'r') as f:
        return [line.strip() for line in f if line.strip()]

def read_completed_urls(completed_file):
    if not os.path.exists(completed_file):
        return set()
    with open(completed_file, 'r') as f:
        return set(line.strip() for line in f if line.strip())

def write_completed_urls(completed_file, urls):
    with open(completed_file, 'a') as f:
        for url in urls:
            f.write(url + '\n')

def write_failed_url(failed_file, url):
    with open(failed_file, 'a') as f:
        f.write(url + '\n')

# =============================================================================
# Page Download Function
# =============================================================================
def download_page(url, destination, driver=None, use_selenium=False):
    try:
        start_time = perf_counter()

        if use_selenium:
            driver.get(url)
            time.sleep(1)  # Optional: wait for JS to render
            page_source = driver.page_source
        else:
            response = session.get(url, timeout=10)
            response.raise_for_status()
            page_source = response.text

        soup = BeautifulSoup(page_source, 'html.parser')
        parsed_url = urlparse(url)
        page_name = parsed_url.netloc + parsed_url.path.replace('/', '_') + '.html'
        page_path = os.path.join(destination, page_name)

        create_directory(destination)

        with open(page_path, 'w', encoding='utf-8') as file:
            file.write(soup.prettify())

        elapsed_time = perf_counter() - start_time
        logging.debug(f"Saved page: {url} to {page_path} (⏱ {elapsed_time:.2f}s)")  # Changed to debug level
        return soup, page_path

    except Exception as e:
        logging.error(f"Error downloading page {url}: {e}")
        return None, None

# =============================================================================
# Website Download Function
# =============================================================================
def download_website(url, destination, max_pages=1, use_selenium=False, driver=None):
    allowed_domain = urlparse(url).netloc
    to_download = [(url, destination)]
    downloaded = set()

    with tqdm(total=max_pages, desc="Downloading pages", unit="page", leave=False) as pbar:
        while to_download and len(downloaded) < max_pages:
            current_url, current_dest = to_download.pop()
            if urlparse(current_url).netloc != allowed_domain:
                continue
            if current_url in downloaded:
                continue

            downloaded.add(current_url)
            soup, page_path = download_page(current_url, current_dest, driver, use_selenium)
            pbar.update(1)

# =============================================================================
# Batching Logic
# =============================================================================
def batch_process(urls, batch_size, download_destination, use_selenium_flag, completed_file, failed_file):
    completed_urls = read_completed_urls(completed_file)
    urls_to_process = [url for url in urls if url not in completed_urls]

    logging.info(f"Starting with {len(urls_to_process)} URLs...\n")

    driver = get_selenium_driver() if use_selenium_flag else None  # Open the driver once before processing

    with tqdm(total=len(urls_to_process), desc="Total Progress", unit="URL") as total_bar:
        for batch_index in range(0, len(urls_to_process), batch_size):
            batch = urls_to_process[batch_index:batch_index + batch_size]
            completed_in_batch = []

            with tqdm(total=len(batch), desc=f"Batch {batch_index // batch_size + 1}", unit="URL", leave=False) as batch_bar:
                for url in batch:
                    try:
                        download_website(url, download_destination, use_selenium=use_selenium_flag, driver=driver)
                        completed_in_batch.append(url)
                        batch_bar.update(1)
                        total_bar.update(1)
                    except Exception as e:
                        logging.error(f"Failed to download {url}: {e}")
                        write_failed_url(failed_file, url)
                        batch_bar.update(1)
                        total_bar.update(1)

            write_completed_urls(completed_file, completed_in_batch)
            logging.info(f"Batch {batch_index // batch_size + 1} completed. Saved progress.")
            time.sleep(0)

    if driver:
        driver.quit()  # Close the browser only once after all batches are processed

# =============================================================================
# Retry Failed URLs Once
# =============================================================================
def retry_failed_urls(download_destination, use_selenium_flag, completed_file, failed_file):
    if not os.path.exists(failed_file):
        logging.info("No failed URLs to retry.")
        return

    with open(failed_file, 'r') as f:
        failed_urls = list(set([line.strip() for line in f if line.strip()]))


    if not failed_urls:
        logging.info("Failed URL list is empty.")
        return

    logging.info(f"Retrying {len(failed_urls)} failed URLs...")

    driver = get_selenium_driver() if use_selenium_flag else None
    succeeded = []
    still_failed = []

    with tqdm(total=len(failed_urls), desc="Retrying Failed URLs", unit="URL") as retry_bar:
        for url in failed_urls:
            try:
                download_website(url, download_destination, use_selenium=use_selenium_flag, driver=driver)
                succeeded.append(url)
            except Exception as e:
                logging.error(f"Retry failed for {url}: {e}")
                still_failed.append(url)
            retry_bar.update(1)

    if driver:
        driver.quit()

    if succeeded:
        write_completed_urls(completed_file, succeeded)
        logging.info(f"{len(succeeded)} URLs succeeded on retry.")

    with open(failed_file, 'w') as f:
        for url in still_failed:
            f.write(url + '\n')

    logging.info(f"{len(still_failed)} URLs still failed after retry.")

# =============================================================================
# Main Execution
# =============================================================================
if __name__ == "__main__":
    url_file_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\Cricket\schedule_fixtures_links.txt"
    download_destination = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\Cricket\html"
    use_selenium = 'y'
    batch_size = 10
    completed_file = "completed_urls.txt"
    failed_file = "failed_urls.txt"

    if not os.path.isfile(url_file_path):
        logging.error("URL file does not exist.")
        exit(1)

    urls = read_urls_from_file(url_file_path)
    use_selenium_flag = use_selenium.lower() == 'y'

    logging.info(f"Loaded {len(urls)} total URLs.")
    batch_process(urls, batch_size, download_destination, use_selenium_flag, completed_file, failed_file)

    retry_failed_urls(download_destination, use_selenium_flag, completed_file, failed_file)

    logging.info("All processing complete.")

2025-04-19 23:13:23,715 - INFO - Loaded 10759 total URLs.
2025-04-19 23:13:23,726 - INFO - Starting with 6039 URLs...

Total Progress:   0%|          | 0/6039 [00:00<?, ?URL/s]


Total Progress:   0%|          | 1/6039 [00:04<7:28:39,  4.46s/URL]


Total Progress:   0%|          | 2/6039 [00:07<5:48:50,  3.47s/URL]


Total Progress:   0%|          | 3/6039 [00:09<4:43:37,  2.82s/URL]


Total Progress:   0%|          | 4/6039 [00:11<4:12:49,  2.51s/URL]


Total Progress:   0%|          | 5/6039 [00:13<3:54:17,  2.33s/URL]


Total Progress:   0%|          | 6/6039 [00:15<4:01:28,  2.40s/URL]


Total Progress:   0%|          | 7/6039 [00:42<17:04:09, 10.19s/URL]


Total Progress:   0%|          | 8/6039 [00:44<12:43:06,  7.59s/URL]


Total Progress:   0%|          | 9/6039 [00:46<10:00:33,  5.98s/URL]


Total Progress:   0%|          | 10/6039 [00:48<8:03:35,  4.81s/URL]2025-04-19 23:14:14,069 - INFO - Batch 1 completed. Saved progress.



Total Progress:   0%|          | 11/6039 [00:51<6

In [7]:
import re

# Path to your saved HTML file
file_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\Cricket\html\www.espncricinfo.com_series_karnataka-premier-league-2018-1154497_match-schedule-fixtures.html" # Update with actual path
from bs4 import BeautifulSoup
base_url = "https://www.espncricinfo.com"

# Read HTML content
with open(file_path, "r", encoding="utf-8") as file:
    html_content = file.read()

# Parse with BeautifulSoup
soup = BeautifulSoup(html_content, "html.parser")

# Find all links containing 'scorecard'
scorecard_links = []
for a in soup.find_all("a", href=True):
    href = a["href"]
    if "scorecard" in href.lower():
        full_link = href if href.startswith("http") else base_url + href
        scorecard_links.append(full_link)

# Print full links
print("Found", len(scorecard_links), "scorecard links:")
for link in scorecard_links:
    print(link)

Found 24 scorecard links:
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/bengaluru-blasters-vs-belagavi-panthers-1st-match-1154498/full-scorecard
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/hubli-tigers-vs-bijapur-bulls-2nd-match-1154499/full-scorecard
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/bengaluru-blasters-vs-bellary-tuskers-3rd-match-1154500/full-scorecard
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/hubli-tigers-vs-namma-shivamogga-4th-match-1154501/full-scorecard
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/bellary-tuskers-vs-mysuru-warriors-5th-match-1154502/full-scorecard
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/belagavi-panthers-vs-bijapur-bulls-6th-match-1154503/full-scorecard
https://www.espncricinfo.com/series/karnataka-premier-league-2018-1154497/hubli-tigers-vs-bellary-tuskers-7th-match-11545

In [9]:
import os
from bs4 import BeautifulSoup

# Folder containing your HTML files
folder_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\Cricket\html"  # Update with your folder path
base_url = "https://www.espncricinfo.com"
output_file = "scorecard_links.txt"

all_links = set()  # Use set to avoid duplicate links

# Loop through all files in the folder
for filename in os.listdir(folder_path):
    if filename.endswith(".html"):
        file_path = os.path.join(folder_path, filename)
        with open(file_path, "r", encoding="utf-8") as file:
            html_content = file.read()
            soup = BeautifulSoup(html_content, "html.parser")

            # Extract scorecard links
            for a in soup.find_all("a", href=True):
                href = a["href"]
                if "full-scorecard" in href.lower():
                    full_link = href if href.startswith("http") else base_url + href
                    all_links.add(full_link)

# Write links to a text file
with open(output_file, "w", encoding="utf-8") as out_file:
    for link in sorted(all_links):
        out_file.write(link + "\n")

print(f"Extracted {len(all_links)} scorecard links and saved to {output_file}")

Extracted 81679 scorecard links and saved to scorecard_links.txt


In [1]:
import pandas as pd
import re

# Load your CSV
csv_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\final_all_merged_data.csv"  # Update with your CSV path
df = pd.read_csv(csv_path)

# Assuming match ID is in a column named 'match_id'
match_ids_in_csv = set(df['match_id'].astype(str).unique())

# Read all links from text file
with open("scorecard_links.txt", "r", encoding="utf-8") as f:
    all_links = f.read().splitlines()

# Function to extract match ID from URL
def extract_match_id(url):
    match = re.search(r"(\d+)(?:/full-scorecard)?$", url)
    return match.group(1) if match else None

# Filter links based on match IDs
filtered_links = [
    link for link in all_links
    if extract_match_id(link) in match_ids_in_csv
]

# Save filtered links
with open("filtered_scorecard_links.txt", "w", encoding="utf-8") as f:
    for link in filtered_links:
        f.write(link + "\n")

print(f"Filtered {len(filtered_links)} links that match CSV match IDs.")

C:\Users\ariad\AppData\Local\Temp\ipykernel_14912\3888674509.py:6: DtypeWarning: Columns (1,20,21,36,53) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(csv_path)


Filtered 8976 links that match CSV match IDs.


In [2]:
# Save filtered links with "full-scorecard" replaced by "ball-by-ball-commentary"
with open("filtered_scorecard_links.txt", "w", encoding="utf-8") as f:
    for link in filtered_links:
        modified_link = link.replace("full-scorecard", "ball-by-ball-commentary")
        f.write(modified_link + "\n")

print(f"Filtered {len(filtered_links)} links that match CSV match IDs and updated to ball-by-ball-commentary.")

Filtered 8976 links that match CSV match IDs and updated to ball-by-ball-commentary.


In [4]:
import os
import time
import re
from tqdm import tqdm

# === CONFIGURATION ===
URLS_FILE = "filtered_scorecard_links.txt"
PROCESSED_FILE = "processed.txt"
FAILED_FILE = "failed.txt"
RETRY_FILE = "retry.txt"
SAVE_DIR = "D:\\commentary_html"

# === UTILITY FUNCTIONS ===
def read_lines(filepath):
    if os.path.exists(filepath):
        with open(filepath, "r") as f:
            return [line.strip() for line in f if line.strip()]
    return []

def write_line(filepath, line):
    with open(filepath, "a") as f:
        f.write(f"{line}\n")

def get_match_id(url):
    try:
        return url.split("/")[-2]
    except Exception:
        return None

# === SCRAPER FUNCTION ===
def run_scraper(url, match_id, driver, wait):
    from selenium.webdriver.common.by import By
    import time
    import re

    WAIT_TIME = 0
    SCROLL_STEP = 100
    ad_hider = """
    var ads = document.querySelectorAll("[id*='ad'], [class*='ad']");
    ads.forEach(el => el.style.display = 'none');
    """

    def get_dropdown_options(driver, wait):
        try:
            dropdown = wait.until(EC.element_to_be_clickable((By.XPATH, "//div[contains(@class, 'ds-popper-wrapper')]//span[contains(@class, 'ds-text-tight-s')]")))
            dropdown.click()
            time.sleep(0.2)
            span_elements = wait.until(EC.presence_of_all_elements_located((By.XPATH, "//div[@class='tippy-content']//li[@class='ds-w-full ds-flex']//span")))
            options_text = [span.text.strip() for span in span_elements]
            dropdown.click()
            return options_text
        except:
            return []

    def select_dropdown_option(driver, wait, option_text):
        try:
            dropdown = wait.until(EC.element_to_be_clickable((By.XPATH, "//div[contains(@class, 'ds-popper-wrapper')]//span[contains(@class, 'ds-text-tight-s')]")))
            dropdown.click()
            time.sleep(0.2)
            if "Innings" in option_text:
                option = wait.until(EC.element_to_be_clickable((By.XPATH, f"//div[@class='tippy-content']//li//span[text()='{option_text}']")))
            else:
                option = wait.until(EC.element_to_be_clickable((By.XPATH, f"//div[@class='tippy-content']//li//span[contains(text(), '{option_text}')]")))
            option.click()
            time.sleep(0.2)
        except:
            raise

    def scroll_and_save(driver, innings_name, it, folder_path):
        print(f"🔃 Scrolling to load commentary for: {innings_name}")
        end_over_1_seen = False
        post_seen_scrolls = 0
        scrolls_times = 0
        pattern = re.compile(r"\bend of over 1\b", re.IGNORECASE)
        max_scrolls = 2000

        for _ in range(max_scrolls):
            if "super over" in innings_name.lower():
                if scrolls_times < 50:
                    driver.execute_script(f"window.scrollBy(0, {SCROLL_STEP});")
                break
                
            if scrolls_times < 50:
                driver.execute_script(f"window.scrollBy(0, {SCROLL_STEP});")
                scrolls_times+=1
                time.sleep(WAIT_TIME)
            else:
                driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
                time.sleep(0)

            if not end_over_1_seen and pattern.search(driver.page_source):
                end_over_1_seen = True
                post_seen_scrolls = 0
                print("✅ Found exact 'end of over 1'.")

            if end_over_1_seen:
                post_seen_scrolls += 1
                if post_seen_scrolls >= 50:
                    print("🛑 Scrolled 50 times after seeing 'end of over 1'. Stopping.")
                    break
        else:
            print("⚠️ Never found 'end of over 1' after full scroll.")
            return "retry"

        os.makedirs(folder_path, exist_ok=True)
        safe_name = re.sub(r'[^A-Za-z0-9_]', '_', innings_name)
        with open(os.path.join(folder_path, f"{safe_name}_[{it+1}]_commentary.html"), "w", encoding="utf-8") as f:
            f.write(driver.page_source)
        return "ok"

    print(f"\n🌐 Processing: {url}")
    try:
        driver.get(url)
        time.sleep(0.2)
        options_list = get_dropdown_options(driver, wait)

        if not options_list:
            raise Exception("Dropdown not found or empty")

        for it, option in enumerate(options_list):
            driver.refresh()
            time.sleep(0.2)
            select_dropdown_option(driver, wait, option)
            driver.execute_script(ad_hider)
            time.sleep(1)
            result = scroll_and_save(driver, option, it, os.path.join(SAVE_DIR, match_id))
            if result == "retry":
                return "retry"

        print(f"✅ Success: {match_id}")
        return "ok"
    except Exception as e:
        print(f"❌ Failed: {match_id} due to {e}")
        return "fail"

# === MAIN DRIVER ===
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager

urls = read_lines(URLS_FILE)
processed = set(read_lines(PROCESSED_FILE))
failed = set(read_lines(FAILED_FILE))
retry = set(read_lines(RETRY_FILE))
# Set up the driver
options = Options()
options.add_argument("--start-maximized")
# options.add_argument("--headless")  # Uncomment for headless mode
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
wait = WebDriverWait(driver, 15)

for url in tqdm(urls, desc="Processing URLs", unit="url"):
    match_id = get_match_id(url)
    if not match_id:
        print(f"⚠️ Skipping invalid URL: {url}")
        continue
    if match_id in processed:
        print(f"🔁 Already done: {match_id}")
        continue
    if match_id in retry:
        print(f"🔁 Added to retry: {match_id}")
        continue
    if match_id in failed:
        print(f"🚫 Previously failed: {match_id}")
        continue

    retry_count = 0
    while retry_count < 2:
        result = run_scraper(url, match_id, driver, wait)
        if result == "ok":
            write_line(PROCESSED_FILE, match_id)
            break
        elif result == "retry":
            print(f"🔁 Retrying: {match_id}")
            retry_count += 1
            driver.refresh()
            time.sleep(0.5)
        else:
            write_line(FAILED_FILE, match_id)
            break
    else:
        print(f"⚠️ Moved to retry.txt after 2 failed attempts: {match_id}")
        write_line(RETRY_FILE, match_id)

driver.quit()
print("\n🏁 Batch processing completed.")

Processing URLs:   0%|          | 0/8976 [00:00<?, ?url/s]

🔁 Already done: hong-kong-vs-malaysia-10th-match-1217747
🔁 Already done: hong-kong-vs-nepal-3rd-match-1217740
🔁 Already done: hong-kong-vs-singapore-8th-match-1217745
🔁 Already done: malaysia-vs-singapore-5th-match-1217742
🔁 Already done: thailand-vs-hong-kong-6th-match-1217743
🔁 Already done: thailand-vs-malaysia-4th-match-1217741
🔁 Already done: thailand-vs-nepal-7th-match-1217744
🔁 Already done: thailand-vs-singapore-1st-match-1217738
🔁 Already done: bhutan-vs-indonesia-2nd-match-group-a-1418181
🔁 Already done: bhutan-vs-maldives-7th-place-play-off-1418193
🔁 Already done: bhutan-vs-saudi-arabia-5th-match-group-a-1418184
🔁 Already done: cambodia-vs-china-qualifying-group-1418177
🔁 Already done: cambodia-vs-indonesia-6th-match-group-a-1418185
🔁 Already done: cambodia-vs-myanmar-qualifying-group-1418176
🔁 Already done: cambodia-vs-saudi-arabia-final-1418197
🔁 Already done: cambodia-vs-singapore-2nd-semi-final-1418195
🔁 Already done: indonesia-vs-saudi-arabia-9th-match-group-a-1418188
🔁

Processing URLs:   3%|▎         | 271/8976 [00:39<21:21,  6.79url/s]

⚠️ Never found 'end of over 1' after full scroll.
✅ Success: india-women-vs-malaysia-women-1st-quarter-final-1399055
🔁 Already done: india-women-vs-sri-lanka-women-final-1399062
🔁 Already done: pakistan-women-vs-sri-lanka-women-2nd-semi-final-1399060
🔁 Already done: sri-lanka-women-vs-thailand-women-3rd-quarter-final-1399057
🔁 Already done: england-vs-australia-1st-odi-1119537
🔁 Already done: england-vs-australia-2nd-odi-1119538
🔁 Already done: england-vs-australia-3rd-odi-1119539
🔁 Already done: england-vs-australia-4th-odi-1119540
🔁 Already done: england-vs-australia-5th-odi-1119541
🔁 Already done: england-vs-australia-only-t20i-1119542
🔁 Already done: india-vs-australia-1st-odi-1119496
🔁 Already done: india-vs-australia-1st-t20i-1119501
🔁 Already done: india-vs-australia-2nd-odi-1119497
🔁 Already done: india-vs-australia-2nd-t20i-1119502
🔁 Already done: india-vs-australia-3rd-odi-1119498
🔁 Already done: india-vs-australia-4th-odi-1119499
🔁 Already done: india-vs-australia-5th-odi-11

Processing URLs:   4%|▍         | 388/8976 [02:50<1:13:55,  1.94url/s]

...

Processing URLs:  95%|█████████▌| 8559/8976 [47:20<01:23,  5.01url/s]

⚠️ Never found 'end of over 1' after full scroll.
✅ Success: namibia-vs-nepal-116th-match-1341976
🔁 Already done: namibia-vs-nepal-119th-match-1341979
🔁 Already done: namibia-vs-nepal-92nd-match-1322031
🔁 Already done: namibia-vs-nepal-95th-match-1322034
🔁 Already done: namibia-vs-oman-49th-match-1290881
🔁 Already done: namibia-vs-oman-61st-match-1302617
🔁 Already done: namibia-vs-oman-64th-match-1302620
🔁 Already done: namibia-vs-oman-66th-match-1302622
🔁 Already done: namibia-vs-papua-new-guinea-109th-match-1341969
🔁 Already done: namibia-vs-papua-new-guinea-112th-match-1341972
🔁 Already done: namibia-vs-papua-new-guinea-11th-match-1199229
🔁 Already done: namibia-vs-papua-new-guinea-12th-match-1199230
🔁 Already done: namibia-vs-scotland-115th-match-1341975
🔁 Already done: namibia-vs-scotland-118th-match-1341978
🔁 Already done: namibia-vs-scotland-122nd-match-1358074
🔁 Already done: namibia-vs-scotland-125th-match-1358077
🔁 Already done: namibia-vs-united-arab-emirates-20th-match-1211

Processing URLs: 100%|██████████| 8976/8976 [48:06<00:00,  3.11url/s]

✅ Found exact 'end of over 1'.
🛑 Scrolled 50 times after seeing 'end of over 1'. Stopping.
✅ Success: ireland-vs-zimbabwe-3rd-t20i-1168522
🔁 Already done: netherlands-vs-zimbabwe-1st-odi-1188377
🔁 Already done: netherlands-vs-zimbabwe-1st-t20i-1188379
🔁 Already done: netherlands-vs-zimbabwe-2nd-odi-1188378
🔁 Already done: netherlands-vs-zimbabwe-2nd-t20i-1188380
🔁 Already done: south-africa-vs-zimbabwe-1st-odi-1144146
🔁 Already done: south-africa-vs-zimbabwe-1st-t20i-1144149
🔁 Already done: south-africa-vs-zimbabwe-2nd-odi-1144147
🔁 Already done: south-africa-vs-zimbabwe-2nd-t20i-1144150
🔁 Already done: south-africa-vs-zimbabwe-3rd-odi-1144148
🔁 Already done: south-africa-vs-zimbabwe-only-test-1122310
🔁 Already done: australia-vs-pakistan-2nd-match-1142914
🔁 Already done: australia-vs-pakistan-5th-match-1142917
🔁 Already done: australia-vs-pakistan-final-1142919
🔁 Already done: zimbabwe-vs-australia-3rd-match-1142915
🔁 Already done: zimbabwe-vs-australia-6th-match-1142918
🔁 Already don


🏁 Batch processing completed.


In [5]:
import re

filename = "1st_Innings_[3]_commentary.html"
match = re.search(r"\[(\d+)\]", filename)

if match:
    number = int(match.group(1))
    print(number)  # Output: 3


3


In [16]:
import os
import re
import pandas as pd
import logging
from bs4 import BeautifulSoup
from tqdm import tqdm
import random

# ---------------------- CONFIGURATION ----------------------
base_dir = r"D:\commentary_html"               # Root folder of all HTML files
output_dir = r"D:\commentary_matches"           # Output folder for CSVs
processed_log_file = r"D:\commentary_matches\processed_files.log"  # Track processed files

# ---------------------- LOGGING SETUP ----------------------
logging.basicConfig(
    filename='processing.log',
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s'
)

# ---------------------- INITIAL SETUP ----------------------
os.makedirs(output_dir, exist_ok=True)

if os.path.exists(processed_log_file):
    with open(processed_log_file, "r") as f:
        processed_files = set(f.read().splitlines())
else:
    processed_files = set()

# ---------------------- NORMALIZATION MAPS AND PATTERNS ----------------------
ball_length_normalize_map = {
    "short-pitched": "short",
    "shortpitched": "short",
    "short": "short",
    "overpitched": "full",
    "over pitched": "full",
    "over-pitched": "full",
    "good length": "good length",
    "blockhole": "block hole",
    "block hole": "block hole",
    "back of a length": "back of length",
    "flatter": "good length",
    "back of length": "back of length",
    "length": "good length",
    "full": "full",
    "steers": "steer",
    "full toss": "full toss",
    "on the hip": "short",
    "low full toss": "low full toss",
    "yorker": "yorker",
    "half-volley": "half-volley",
    "slot": "slot",
    "bouncer": "bouncer",
}

ball_line_normalize_map = {
    "outside off": "outside off",
    "wide": "outside off",
    "perfect line": "outside off",
    "top of off": "on off stump",
    "top of middle": "on middle stump",
    "top of leg": "on leg stump",
    "outside the off": "outside off",
    "on off": "on off stump",
    "on middle": "on middle stump",
    "on leg": "on leg stump",
    "leg side delivery": "on leg stump",
    "off side delivery": "on off stump",
    "into leg": "on leg stump",
    "around off": "on off stump",
    "around leg": "on leg stump",
    "around middle": "on middle stump",
    "down leg": "down the leg",
    "on middel": "on middle stump",
    "middle line": "on middle stump",
    "off line": "on off stump",
    "line and length": random.choice(["on off stump", "outside off"]),
    "good line and length": random.choice(["on off stump", "outside off"]),
    "leg line": "on leg stump",
    "middle stump line": "on middle stump",
    "leg stump line": "on leg stump",
    "off stump line": "on off stump",
    "outside leg": "outside leg stump",
    "leg and middle": "on middle and leg",
    "off and middle": "on middle and off",
    "on line": "on the stumps",
    "middle and off": "on middle and off",
    "middle and leg": "on middle and leg",
    "on the leg and middle": "on middle and leg",
    "on the off and middle": "on middle and off",
    "on the middle and off": "on middle and off",
    "on the middle and leg": "on middle and leg",
    "around leg and middle": "on middle and leg",
    "around off and middle": "on middle and off",
    "around middle and off": "on middle and off",
    "around middle and leg": "on middle and leg",
    "down the leg": "down the leg",
    "on the pads" : "on leg stump",
    "off the pads": "on leg stump",
    "corridor of uncertainty": "corridor of uncertainty",
    "bodyline": "bodyline",
    "on the stumps": "on the stumps",
    "off stump": "on off stump",
    "leg stump": "on leg stump",
    "middle stump": "on middle stump",
    "on the middle": "on middle stump",
    "on the legs": "on leg stump",
    "on the off": "on off stump",
    "on the leg": "on leg stump"
}

shot_played_normalize_map = {
    "pulls": "pull",
    "pull": "pull",
    "played off the pads": "flick",
    "cover drive": "cover drive",
    "straight drive": "straight drive",
    "off drive": "off drive",
    "square drive": "square drive",
    "on drive": "on drive",
    "pushed": "defense",
    "beats": "beaten",
    "push": "defense",
    "flicked": "flick",
    "flick": "flick",
    "hooked": "hook",
    "hook": "hook",
    "clipped": "clips",
    "whipped": "whips",
    "clip": "clips",
    "whip": "whips",
    "driven": "drive",
    "drive": "drive",
    "cut": "cut",
    "swept": "sweep",
    "sweep": "sweep",
    "glanced": "glance",
    "glance": "glance",
    "leg glance": "leg glance",
    "blocked": "defense",
    "defended": "defense",
    "defense": "defense",
    "edge": "edge",
    "punched": "punch",
    "punch": "punch",
    "dabbed": "dab",
    "dab": "dab",
    "slogged": "slog",
    "slog": "slog",
    "drove": "drive",
    "ramped": "ramp",
    "ramp": "ramp",
    "loft": "loft",
    "tap": "defense",
    "upper cut": "upper cut",
    "scooped": "scoop",
    "scoop": "scoop",
    "paddled": "paddle",
    "paddle": "paddle",
    "glided": "glide",
    "glide": "glide",
    "nudged": "nudge",
    "nudge": "nudge",
    "back to the bowler": "defense",
    "work": "work",
    "tapped": "defense",
    "defending": "defense",
    "defend": "defense",
    "slice": "cut",
    "sliced": "cut",
    "lofted": "lofted drive",
    "beaten": "beated",
    "left alone": "leave",
    "leave": "leave",
    "shoulders arms": "defense",
    "helicopter shot": "helicopter shot",
    "french cut": "french cut",
    "late cut": "late cut",
    "switch hit": "switch hit",
    "dilscoop": "dilscoop",
    "works it": "works it",
    "played on": "inside edge",
    "edged": "edged",
    "through to keeper": "leave",
    "thgrough to keeper": "leave",
    "reverse hit": "reverse hit",
    "inside edge": "inside edge",
    "outside edge": "outside edge",
    "into his pads": "inside edge",
    "into her pads": "inside edge",
    "plays and missed": "beaten",
    "plays but misses": "beaten",
    "play's but misses": "beaten",
    "play's and missed": "beaten",
    "plays and misses": "beaten",
    "play's and misses": "beaten",
    "outside egde": "outside edge"
}

shot_direction_normalize_map = {
    "mid-on": "mid-on",
    "mid off": "mid-off",
    "mid-off": "mid-off",
    "mid on": "mid-on",
    "mid wkt": "mid wicket",
    "midwicket": "mid wicket",
    "mid wicket": "mid wicket",
    "deep mid wkt": "deep mid wicket",
    "deep midwicket": "deep mid wicket",
    "deep mid wicket": "deep mid wicket",
    "short midwicket": "short mid wicket",
    "short mid wicket": "short mid wicket",
    "silly mid-off": "silly mid-off",
    "silly mid off": "silly mid-off",
    "silly mid-on": "silly mid-on",
    "silly mid on": "silly mid-on",
    "silly point": "silly point",
    "off side": "off side",
    "leg side": "leg side",
    "on side": "on side",
    "long-on": "long on",
    "long on": "long on",
    "long-off": "long off",
    "long off": "long off",
    "cover": "cover",
    "extra cover": "extra cover",
    "deep extra cover": "deep extra cover",
    "short extra cover": "short extra cover",
    "deep cover": "deep cover",
    "short cover": "short cover",
    "sweeper cover": "sweeper cover",
    "sweeper": "sweeper",
    "point": "point",
    "cover point": "cover point",
    "deep point": "deep point",
    "deep cover point": "deep cover point",
    "deep backward point": "deep backward point",
    "forward point": "forward point",
    "backward point": "backward point",
    "square leg": "square leg",
    "sqaure leg": "square leg",
    "deep square leg": "deep square leg",
    "deep forward square": "deep forward square",
    "deep backward square": "deep backward square",
    "deep backward square leg": "deep backward square leg",
    "deep forward square leg": "deep forward square leg",
    "backward square leg": "backward square leg",
    "forward square leg": "forward square leg",
    "short leg": "short leg",
    "backward short leg": "backward short leg",
    "fine leg": "fine leg",
    "short fine": "short fine leg",
    "short fine leg": "short fine leg",
    "deep fine leg": "deep fine leg",
    "square fine leg": "square fine leg",
    "long leg": "long leg",
    "straight fine leg": "straight fine leg",
    "third man": "third man",
    "3rd man": "third man",
    "short third man": "short third man",
    "short 3rd man": "short third man",
    "deep third man": "deep third man",
    "deep 3rd man": "deep third man",
    "square third man": "square third man",
    "square 3rd man": "square third man",
    "fine third man": "fine third man",
    "fine 3rd man": "fine third man",
    "gully": "gully",
    "deep gully": "deep gully",
    "slip": "slip",
    "slips": "slips",
    "fly slip": "fly slip",
    "leg slip": "leg slip",
    "leg gully": "leg gully",
    "past the bowler": "down the ground",
    "over the bowler": "down the ground",
    "straight boundary": "down the ground",
    "down town": "down the ground",
    "down the ground": "down the ground",
    "straight down the ground": "straight down the ground",
    "straight mid-on": "straight mid-on",
    "deep long off": "deep long off",
    "deep third man": "deep third man",
    "over the keeper": "over the keeper",
    "over the slips": "over the slips",
    "back to bowler": "back to bowler",
    "towards the bowler": "back to the bowler",
    "deep forward mid wicket": "deep forward mid wicket",
    "sweeper mid wicket": "sweeper mid wicket",
    "short mid off": "short mid-off",
    "short mid-off": "short mid-off",
    "deep mid off": "deep mid-off",
    "deep mid-off": "deep mid-off",
    "short mid on": "short mid-on",
    "short mid-on": "short mid-on",
    "deep mid on": "deep mid-on",
    "deep mid-on": "deep mid-on",
    "wide long off": "wide long off",
    "straight long off": "straight long off",
    "wide long on": "wide long on",
    "straight long on": "straight long on",
    "cow corner": "cow corner",
    "behind square": "behind square",
    "behind point": "behind point",
    "over midwicket": "over mid wicket",
    "over cover": "over cover",
    "over long on": "over long on",
    "over long off": "over long off"
}


def create_pattern_with_suffixes(norm_map):
    terms = sorted(norm_map.keys(), key=lambda x: -len(x))
    # allow common suffixes after base word (customize suffixes as needed)
    suffixes = r"(s|es|ed|ing|ish|'s|er)?"
    pattern_str = r'\b(' + '|'.join(re.escape(t) for t in terms) + r')' + suffixes + r'\b'
    return re.compile(pattern_str, re.IGNORECASE)

ball_length_pat = create_pattern_with_suffixes(ball_length_normalize_map)
ball_line_pat   = create_pattern_with_suffixes(ball_line_normalize_map)
shot_played_pat = create_pattern_with_suffixes(shot_played_normalize_map)
shot_dir_pat    = create_pattern_with_suffixes(shot_direction_normalize_map)

def extract_terms(text):
    txt = (text or "").lower()
    out = {'ball_length':None,'ball_line':None,'shot_played':None,'shot_direction':None}
    
    m = ball_length_pat.search(txt)
    if m: 
        base_word = m.group(1).lower()  # group(1) is the base matched word without suffix
        out['ball_length'] = ball_length_normalize_map.get(base_word)
        
    m = ball_line_pat.search(txt)
    if m: 
        base_word = m.group(1).lower()
        out['ball_line'] = ball_line_normalize_map.get(base_word)
        
    m = shot_played_pat.search(txt)
    if m: 
        base_word = m.group(1).lower()
        out['shot_played'] = shot_played_normalize_map.get(base_word)
        
    m = shot_dir_pat.search(txt)
    if m: 
        base_word = m.group(1).lower()
        out['shot_direction'] = shot_direction_normalize_map.get(base_word)
        
    return out

def extract_from_first_logic(soup):
    data = []
    for b in soup.find_all(
        "div",
        class_="ds-text-tight-m ds-font-regular ds-flex "
               "ds-px-3 ds-py-2 lg:ds-px-4 lg:ds-py-[10px] "
               "ds-items-start ds-select-none lg:ds-select-auto"
    ):
        try:
            over = b.find("span", class_="ds-text-tight-s").get_text(strip=True)
            combo = b.find("div", class_="ds-leading-[16px]").get_text(strip=True)
            bowler, rest = combo.split("to",1)
            batter, outcome = rest.split(",",1)
            comm = b.find("p", class_="ci-html-content").get_text(strip=True)
            data.append({
                "Over": over,
                "Bowler": bowler.strip(),
                "Batter": batter.strip(),
                "Outcome": outcome.strip(),
                "Commentary": comm
            })
        except:
            continue
    return data

def save_rows_to_match_csv(match_id, rows, output_dir):
    output_path = os.path.join(output_dir, f"{match_id}_enriched.csv")
    df = pd.DataFrame(rows)
    #df = df.drop(columns=["Commentary"])
    if not os.path.exists(output_path):
        df.to_csv(output_path, index=False, mode='w')
    else:
        df.to_csv(output_path, index=False, mode='a', header=False)

from collections import defaultdict

# ---------------------- MAIN PROCESSING LOOP ----------------------
total_files = 0
processed_count = 0
skipped_count = 0
error_count = 0

# Load previously processed match IDs from log
processed_match_ids = set()
if os.path.exists(processed_log_file):
    with open(processed_log_file, encoding="utf-8") as f:
        processed_match_ids = set(line.strip() for line in f if line.strip())

# Step 1: Collect and group files by match_id
files_by_match_id = defaultdict(list)
for root, _, files in os.walk(base_dir):
    for fname in files:
        if fname.endswith("_commentary.html"):
            folder = os.path.basename(os.path.dirname(os.path.join(root, fname)))
            match_id_match = re.search(r"(\d+)$", folder)
            match_id = match_id_match.group(1) if match_id_match else "unknown"
            full_path = os.path.join(root, fname)
            files_by_match_id[match_id].append(full_path)

total_matches = len(files_by_match_id)
print(f"Found {total_matches} matches to process...")

# Step 2: Process each match
for match_id, file_list in tqdm(files_by_match_id.items(), desc="Processing matches"):
    if match_id in processed_match_ids:
        skipped_count += len(file_list)
        continue

    try:
        match_rows = []

        for full_path in file_list:
            fname = os.path.basename(full_path)

            with open(full_path, encoding="utf-8") as f:
                soup = BeautifulSoup(f, "html.parser")

            rows = extract_from_first_logic(soup)
            if not rows:
                skipped_count += 1
                continue

            # Extract inning number from filename
            inning_match = re.search(r"\[(\d+)\]", fname)
            inning_number = int(inning_match.group(1)) if inning_match else None

            for r in rows:
                r["match_id"] = match_id
                r["inning_number"] = inning_number
                r.update(extract_terms(r.get("Commentary", "")))

                if (r.get("shot_played") or "").strip().lower() == "cut":
                    if not r.get("ball_line"):
                        r["ball_line"] = "outside off"
                    if not r.get("ball_length"):
                        r["ball_length"] = "short"

                if (r.get("shot_played") or "").strip().lower() == "sweep":
                    if not r.get("ball_line"):
                        r["ball_line"] = random.choice(["on leg stump", "on middle and leg", "on middle stump"])
                    if not r.get("ball_length"):
                        r["ball_length"] = "full"
                
                if (r.get("shot_played") or "").strip().lower() == "upper cut":
                    if not r.get("ball_line"):
                        r["ball_line"] = "outside off"
                    if not r.get("ball_length"):
                        r["ball_length"] = random.choice(["short", "bouncer"])

                if (r.get("shot_played") or "").strip().lower() in {"glance", "leg glance"}:
                    if not r.get("ball_line"):
                        r["ball_line"] = "leg"
                    if not r.get("ball_length"):
                        r["ball_length"] = random.choice(["good length", "full"])

                if (r.get("shot_played") or "").strip().lower() == "flick":
                    if not r.get("ball_line"):
                        r["ball_line"] = "on leg stump"
                    if not r.get("ball_length"):
                        r["ball_length"] = "good length"

                if (r.get("shot_played") or "").strip().lower() == "pull":
                    if not r.get("ball_length"):
                        r["ball_length"] = random.choice(["short", "bouncer"])
                    if not r.get("ball_line"):
                        r["ball_line"] = random.choice(["on leg stump", "on middle and leg", "on middle stump"])

                if (r.get("shot_played") or "").strip().lower() == "hook":
                    if not r.get("ball_length"):
                        r["ball_length"] = random.choice(["short", "bouncer"])
                    if not r.get("ball_line"):
                        r["ball_line"] = "on leg stump"

                if (r.get("shot_played") or "").strip().lower() == "leave":
                    if not r.get("ball_line"):
                        r["ball_line"] = "outside off"

                if ((r.get("shot_played") or "").strip().lower() == "cover drive" and
                    (r.get("shot_direction") or "").strip().lower() == "cover"):
                    if not r.get("ball_line"):
                        r["ball_line"] = "outside off"
                    if not r.get("ball_length"):
                        r["ball_length"] = "full"
                
                if (r.get("shot_direction") or "").strip().lower() == "cover":
                    if not r.get("ball_line"):
                        r["ball_line"] = "outside off"
                    if not r.get("ball_length"):
                        r["ball_length"] = random.choice(["good length", "full"])

                outcome_raw = (r.get("Outcome") or "").strip().lower()
                outcome = re.sub(r'^\([^)]*\)\s*', '', outcome_raw)
                if outcome == "four runs":
                    r["Outcome"] = 4
                elif outcome == "six runs":
                    r["Outcome"] = 6
                elif outcome == "no run":
                    r["Outcome"] = 0
                elif outcome == "3 runs":
                    r["Outcome"] = 3
                elif outcome == "2 runs":
                    r["Outcome"] = 2
                elif outcome == "5 runs":
                    r["Outcome"] = 5
                elif outcome == "6 runs":
                    r["Outcome"] = 2
                elif outcome == "6 runs":
                    r["Outcome"] = 7
                elif outcome == "1 run":
                    r["Outcome"] = 1
                elif outcome == "out":
                    r["Outcome"] = 0
                # Default to 0 for any form of extras
                elif any(x in outcome for x in ["wide", "leg bye", "leg byes", "bye", "byes"]):
                    r["Outcome"] = 0
                # Handle numeric cases like "1 run", "2 runs" (fallback)
                else:
                    try:
                        r["Outcome"] = int(outcome.split()[0])
                    except:
                        r["Outcome"] = 0
                        
                match_rows.append(r)

            processed_count += 1

        if match_rows:
            save_rows_to_match_csv(match_id, match_rows, output_dir)
            with open(processed_log_file, "a", encoding="utf-8") as logf:
                logf.write(match_id + "\n")
            processed_match_ids.add(match_id)

    except Exception as e:
        logging.error(f"Error processing match_id {match_id}: {str(e)}")
        error_count += 1

print(f"\nProcessing complete. Matches: {total_matches}, Processed files: {processed_count}, Skipped: {skipped_count}, Errors: {error_count}")

Found 8962 matches to process...


Processing matches: 100%|██████████| 8962/8962 [1:25:25<00:00,  1.75it/s]  


Processing complete. Matches: 8962, Processed files: 12812, Skipped: 6502, Errors: 0


In [1]:
import os
import re
import pandas as pd
import logging
from bs4 import BeautifulSoup
from tqdm import tqdm
import random

folder = r"D:\commentary_matches"

# Get all combined CSV files
combined_files = [f for f in os.listdir(folder) if f.endswith("_enriched.csv")]

# Initialize an empty list to store DataFrames
dfs = []

# Read and append each combined CSV
for file in combined_files:
    file_path = os.path.join(folder, file)
    df = pd.read_csv(file_path)
    dfs.append(df)

desired_order = [
    'match_id', 'ball', 'innings', 'striker', 'bowler', 'runs_off_bat', 'Commentary', 'ball_length', 'ball_line', 'shot_played', 'shot_direction'
]

# Concatenate all DataFrames into a single DataFrame
final_df = pd.concat(dfs, ignore_index=True)
final_df.rename(columns={
    'inning_number': 'innings',
    'Over': 'ball',
    'Outcome': 'runs_off_bat',
    'Bowler': 'bowler',
    'Batter': 'striker'
}, inplace=True)
final_df = final_df[desired_order]
output_path = r"D:\commentary_matches\merged_hawkeye.csv"
final_df.to_csv(output_path, index=False)

In [10]:
player_metadata_path = r"D:\commentary_matches\merged_hawkeye.csv"

df_metadata = pd.read_csv(player_metadata_path)
df_metadata.info()
# Count total null values per column
null_counts = df_metadata.isnull().sum()

# Display columns with missing values
null_counts = null_counts[null_counts > 0]

print("Columns with missing values:\n", null_counts)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3268129 entries, 0 to 3268128
Data columns (total 11 columns):
 #   Column          Dtype  
---  ------          -----  
 0   ball            float64
 1   bowler          object 
 2   striker         object 
 3   runs_off_bat    int64  
 4   Commentary      object 
 5   match_id        int64  
 6   innings         int64  
 7   ball_length     object 
 8   ball_line       object 
 9   shot_played     object 
 10  shot_direction  object 
dtypes: float64(1), int64(3), object(7)
memory usage: 274.3+ MB
Columns with missing values:
 Commentary              4
ball_length       1144132
ball_line         1161701
shot_played       1072441
shot_direction    1300640
dtype: int64


In [36]:
import os
import re

# Path to the main directory containing match folders
base_dir = r"D:\commentary_html"

# List to store match numbers with super over HTMLs
super_over_match_nums = []

# Traverse each folder in the base directory
for folder_name in os.listdir(base_dir):
    folder_path = os.path.join(base_dir, folder_name)

    # Ensure it's a folder
    if os.path.isdir(folder_path):
        # Look for any file containing 'Super_Over' in its name (case-insensitive)
        files = os.listdir(folder_path)
        has_super_over = any("super_over" in file.lower() and file.endswith(".html") for file in files)

        if has_super_over:
            # Extract trailing number (match ID) from the folder name
            match = re.search(r'(\d+)$', folder_name)
            if match:
                super_over_match_nums.append(int(match.group(1)))

# Output the match numbers
print("Matches with Super Over commentary files:", super_over_match_nums)


Matches with Super Over commentary files: [571149, 1263472, 1183544, 1475529, 1405125, 1286674, 1380586, 1216493, 1175365, 1473469, 1144530, 902653, 1370791, 1432196, 1400975, 1082625, 1345425, 1412534, 1336982, 729315, 1459720, 1216517, 1178426, 1474411, 1415703, 1405327, 1377763, 1188380, 1190607, 1147733, 423788, 1187669, 1187679, 1187680, 1322362, 366707, 533292, 1388201, 1233463, 1172470, 1422804, 829741, 598017, 1216547, 1469306, 1144172, 1277093, 1442989, 533284, 1254077, 1216512, 598004, 1453519, 1415711, 1334418, 1273422, 1426049]


In [ ]:
import pandas as pd

# Original list of match IDs
super_over_ids = [
    571149, 1263472, 1183544, 1475529, 1405125, 1286674, 1380586, 1216493, 1175365,
    1473469, 1144530, 902653, 1370791, 1432196, 1400975, 1082625, 1345425, 1412534,
    1336982, 729315, 1459720, 1216517, 1178426, 1474411, 1415703, 1405327, 1377763,
    1188380, 1190607, 1147733, 423788, 1187669, 1187679, 1187680, 1322362, 366707,
    533292, 1388201, 1233463, 1172470, 1422804, 829741, 598017, 1216547, 1469306,
    1144172, 1277093, 1442989, 533284, 1254077, 1216512, 598004, 1453519, 1415711,
    1334418, 1273422, 1426049
]

# Load the CSV
csv_path = r"D:\commentary_matches\merged_hawkeye.csv"
df = pd.read_csv(csv_path)

# Ensure match_id column is integer
df['match_id'] = df['match_id'].astype(int)

# Get unique match IDs from CSV
csv_match_ids = set(df['match_id'].unique())

# Filter the list to keep only those present in the CSV
filtered_ids = [mid for mid in super_over_ids if mid in csv_match_ids]

print(f"Filtered list: {filtered_ids}")
print(f"{len(filtered_ids)} match IDs found in the CSV out of {len(super_over_ids)} total.")

In [1]:
import pandas as pd

# Load your CSV
df = pd.read_csv(r"D:\commentary_matches\merged_hawkeye.csv")  # replace with your actual file path

# Ensure sorting for correct sequence
df.sort_values(by=['match_id', 'innings', 'ball'], inplace=True)

def fix_duplicate_balls(group):
    seen = {}
    new_balls = []

    for orig_ball in group['ball']:
        over = int(orig_ball)
        delivery = round((orig_ball - over) * 10)

        # Make sure this ball number hasn't been used already
        while (over, delivery) in seen:
            delivery += 1
        seen[(over, delivery)] = True

        # Construct the new ball number (e.g., 70 + 0.2 = 70.2)
        new_balls.append(round(over + delivery / 10, 1))

    group['ball'] = new_balls
    return group

# Apply the function to each match and innings
df = df.groupby(['match_id', 'innings'], group_keys=False).apply(fix_duplicate_balls)

# Save to CSV or use as needed
df.to_csv(r"D:\commentary_matches\merged_hawkeye_cleaned.csv", index=False)
print("Duplicates fixed and saved to cleaned_file.csv")


C:\Users\ariad\AppData\Local\Temp\ipykernel_18200\3869949382.py:29: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df = df.groupby(['match_id', 'innings'], group_keys=False).apply(fix_duplicate_balls)


Duplicates fixed and saved to cleaned_file.csv


In [5]:
import pandas as pd
import traceback

def safe_load_csv(path):
    try:
        print(f"Loading CSV from {path} ...")
        df = pd.read_csv(path, low_memory=False)
        print(f"Loaded {len(df)} rows.")
        return df
    except Exception as e:
        print(f"Error loading {path}: {e}")
        traceback.print_exc()
        return None

def safe_merge(left_df, right_df, on_cols, how='left', suffixes=('', '_hawk')):
    try:
        # Columns to keep from right_df (excluding the ones you don't want)
        right_cols_to_keep = [
            col for col in right_df.columns 
            if col not in {'bowler', 'striker', 'commentary'} 
            and col not in on_cols  # Don't duplicate merge keys
        ]
        
        # Add back the merge keys
        right_cols_to_keep.extend(on_cols)
        
        merged = pd.merge(
            left_df,
            right_df[right_cols_to_keep],
            on=on_cols,
            how=how,
            suffixes=suffixes
        )
        print(f"Merged on {on_cols} - resulting shape: {merged.shape}")
        return merged
    except Exception as e:
        print(f"Error merging on {on_cols}: {e}")
        traceback.print_exc()
        return None

def main():
    try:
        main_csv_path = r"C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\final_all_merged_data.csv"
        hawk_csv_path = r"D:\commentary_matches\merged_hawkeye_cleaned.csv"

        super_over_matches = [  ]
        # Load data
        main_df = safe_load_csv(main_csv_path)
        hawk_df = safe_load_csv(hawk_csv_path)

        if main_df is None or hawk_df is None:
            print("Failed to load data, exiting.")
            return

        # Standardize columns
        main_df.columns = main_df.columns.str.strip().str.lower()
        hawk_df.columns = hawk_df.columns.str.strip().str.lower()

        # Convert data types
        main_df["match_id"] = main_df["match_id"].astype(str)
        hawk_df["match_id"] = hawk_df["match_id"].astype(str)
        main_df["innings"] = main_df["innings"].astype(int)
        hawk_df["innings"] = hawk_df["innings"].astype(int)
        main_df["ball"] = main_df["ball"].astype(float)
        hawk_df["ball"] = hawk_df["ball"].astype(float)

        main_normal = main_df[~main_df['match_id'].isin(super_over_matches)].copy()
        
        hawk_normal = hawk_df[~hawk_df['match_id'].isin(super_over_matches)].copy()

        # Merge normal matches (on match_id, innings, ball)
        merged_normal = safe_merge(
            main_normal,
            hawk_normal,
            on_cols=['match_id', 'innings', 'ball', 'runs_off_bat']
        )
        if merged_normal is None:
            print("Normal merge failed, exiting.")
            return

        # Combine results
        final_df = pd.concat([merged_normal], ignore_index=True)
        
        print(f"Final merged dataframe shape: {final_df.shape}")
        print("Columns in final output:", final_df.columns.tolist())

        # Save results
        output_path = r"D:\commentary_matches\ball_by_ball_data.csv"
        desired_order = ['match_id', 'season', 'start_date', 'venue', 'innings', 'ball', 'batting_team', 'bowling_team', 'striker', 'non_striker', 'bowler', 'ball_length', 'ball_line', 'shot_played', 'shot_direction', 'runs_off_bat', 'extras', 'wides', 'noballs', 'byes', 'legbyes', 'penalty', 'wicket_type', 'player_dismissed', 'other_wicket_type', 'other_player_dismissed', 'wicket', 'striker balls faced', 'total striker runs', 'player out runs', 'player out balls faced', 'gender', 'event', 'match_number', 'toss_winner', 'toss_decision', 'player_of_match', 'player_of_match.1', 'winner', 'winner_runs', 'winner_wickets', 'outcome', 'format', 'type', 'full name_striker', 'country_striker', 'batting style_striker', 'bowling style_striker', 'playing role_striker', 'major teams_striker', 'image url_striker', 'full name_bowler', 'country_bowler', 'batting style_bowler', 'bowling style_bowler', 'playing role_bowler', 'major teams_bowler', 'image url_bowler']
        final_df = final_df[desired_order]
        final_df.to_csv(output_path, index=False)
        print(f"Merge completed successfully. Output saved to {output_path}")

    except Exception as e:
        print(f"Unexpected error: {e}")
        traceback.print_exc()

if __name__ == "__main__":
    main()

Loading CSV from C:\Users\ariad\OneDrive\Desktop\Projects\International Cricket Analysis - Tableau\final_all_merged_data.csv ...
Loaded 4431800 rows.
Loading CSV from D:\commentary_matches\merged_hawkeye_cleaned.csv ...
Loaded 3268128 rows.
Merged on ['match_id', 'innings', 'ball', 'runs_off_bat'] - resulting shape: (4431818, 58)
Final merged dataframe shape: (4431818, 58)
Columns in final output: ['match_id', 'season', 'start_date', 'venue', 'innings', 'ball', 'batting_team', 'bowling_team', 'striker', 'non_striker', 'bowler', 'runs_off_bat', 'extras', 'wides', 'noballs', 'byes', 'legbyes', 'penalty', 'wicket_type', 'player_dismissed', 'other_wicket_type', 'other_player_dismissed', 'wicket', 'striker balls faced', 'total striker runs', 'player out runs', 'player out balls faced', 'gender', 'event', 'match_number', 'toss_winner', 'toss_decision', 'player_of_match', 'winner', 'winner_runs', 'winner_wickets', 'outcome', 'format', 'type', 'full name_striker', 'country_striker', 'batting s

In [6]:
player_metadata_path = r"D:\commentary_matches\ball_by_ball_data.csv"

df_metadata = pd.read_csv(player_metadata_path)
df_metadata.info()
# Count total null values per column
null_counts = df_metadata.isnull().sum()

# Display columns with missing values
null_counts = null_counts[null_counts > 0]

print("Columns with missing values:\n", null_counts)

C:\Users\ariad\AppData\Local\Temp\ipykernel_11208\2073924014.py:3: DtypeWarning: Columns (1,11,12,13,14,24,25,37,41) have mixed types. Specify dtype option on import or set low_memory=False.
  df_metadata = pd.read_csv(player_metadata_path)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4431818 entries, 0 to 4431817
Data columns (total 58 columns):
 #   Column                  Dtype  
---  ------                  -----  
 0   match_id                int64  
 1   season                  object 
 2   start_date              object 
 3   venue                   object 
 4   innings                 int64  
 5   ball                    float64
 6   batting_team            object 
 7   bowling_team            object 
 8   striker                 object 
 9   non_striker             object 
 10  bowler                  object 
 11  ball_length             object 
 12  ball_line               object 
 13  shot_played             object 
 14  shot_direction          object 
 15  runs_off_bat            int64  
 16  extras                  int64  
 17  wides                   float64
 18  noballs                 float64
 19  byes                    float64
 20  legbyes                 float64
 21  penalty                 float64

In [7]:
import pandas as pd
player_metadata_path = r"D:\commentary_matches\ball_by_ball_data.csv"
df_metadata = pd.read_csv(player_metadata_path)
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', 1000)  # Prevent line wrapping
df_metadata.sample(5)

C:\Users\ariad\AppData\Local\Temp\ipykernel_11208\338233017.py:3: DtypeWarning: Columns (1,11,12,13,14,24,25,37,41) have mixed types. Specify dtype option on import or set low_memory=False.
  df_metadata = pd.read_csv(player_metadata_path)


match_id   season  start_date                                          venue  innings   ball    batting_team    bowling_team            striker   non_striker        bowler ball_length    ball_line shot_played    shot_direction  runs_off_bat  extras  wides  noballs  byes  legbyes  penalty wicket_type player_dismissed other_wicket_type other_player_dismissed  wicket  striker balls faced  total striker runs  player out runs  player out balls faced  gender                                     event  match_number     toss_winner toss_decision    player_of_match player_of_match.1          winner  winner_runs  winner_wickets outcome format       type          full name_striker country_striker batting style_striker         bowling style_striker playing role_striker                                major teams_striker                                  image url_striker         full name_bowler country_bowler batting style_bowler    bowling style_bowler playing role_bowler  \
126308    1473446     2025  2025-03-29               Narendra Modi Stadium, Ahmedabad        1    6.4  Gujarat Titans  Mumbai Indians    B Sai Sudharsan  Shubman Gill     HH Pandya        full  outside off       drive     sweeper cover             1       0    NaN      NaN   NaN      NaN      NaN         NaN              NaN               NaN                    NaN       0                 22.0                34.0              NaN                     NaN    male                     Indian Premier League           9.0  Mumbai Indians         field  M Prasidh Krishna               NaN  Gujarat Titans         36.0             NaN     NaN    T20  Fran(IPL)     Bhardwaj Sai Sudharsan           India         Left hand Bat                      Legbreak     Top order Batter  India, Gujarat Titans, Chepauk Super Gillies, ...  https://img1.hscicdn.com/image/upload/f_auto,t...   Hardik Himanshu Pandya          India       Right hand Bat   Right arm Medium fast          Allrounder   
2510857   1447493     2024  2024-09-06                    YSD-UKM Cricket Oval, Bangi        2    8.1       Singapore          Kuwait         WA Simpson     AE Paraam   Shiraz Khan         NaN          NaN         NaN               NaN             0       2    NaN      NaN   NaN      2.0      NaN         NaN              NaN               NaN                    NaN       0                 13.0                 8.0              NaN                     NaN    male  ICC Men's T20 World Cup Asia Qualifier A          17.0       Singapore         field                NaN               NaN       Singapore          NaN             5.0     NaN    T20       Intl  William Arlington Simpson       Singapore        Right hand Bat                           NaN                  NaN                                          Singapore                                                NaN      Shiraz Khan Shereef         Kuwait       Right hand Bat         Legbreak Googly          Allrounder   
1160832    300426  2007/08  2007-12-26                                      Eden Park        1   25.6      Bangladesh     New Zealand  Mohammad Ashraful   Tamim Iqbal    DL Vettori         NaN  outside off       drive  deep extra cover             1       0    NaN      NaN   NaN      NaN      NaN         NaN              NaN               NaN                    NaN       0                 48.0                57.0              NaN                     NaN    male      Bangladesh in New Zealand ODI Series           1.0     New Zealand         field             JM How               NaN     New Zealand          NaN             6.0     NaN    ODI       Intl          Mohammad Ashraful      Bangladesh        Right hand Bat  Right arm Offbreak, Legbreak  Middle order Batter  Bangladesh, Asia XI, Bangladesh A, Central Zon...  https://img1.hscicdn.com/image/upload/f_auto,t...      Daniel Luca Vettori    New Zealand        Left hand Bat  Slow Left arm Orthodox          Allrounder   
2460743   1435632     2024  2024-06-03  Gahanga International Cri

In [5]:
import pandas as pd

# Load the dataset
player_metadata_path = r"D:\commentary_matches\ball_by_ball_data.csv"
df_metadata = pd.read_csv(player_metadata_path)

# Filter rows where 'winner' is null and 'batting_team' is 'India'
df_null_event = df_metadata[df_metadata['batting_team'] == 'India']
#df_null_event = df_metadata[df_metadata['winner'].isnull() & (df_metadata['batting_team'] == 'India')]

# Drop duplicate match_id values
df_unique_matches = df_null_event.drop_duplicates(subset=['match_id'])

# Display 10 random unique rows based on match_id
df123 = df_unique_matches.sample(n=10, random_state=42)
unique_match_count = df_null_event['match_id'].nunique()

print("Total unique matches where winner is null and batting team is India:", unique_match_count)
# Show full columns in VS Code
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', 1000)  # Prevent line wrapping

df123  # Display the DataFrame

C:\Users\ariad\AppData\Local\Temp\ipykernel_18200\749052230.py:5: DtypeWarning: Columns (1,20,21,36,53,54,55,56,57) have mixed types. Specify dtype option on import or set low_memory=False.
  df_metadata = pd.read_csv(player_metadata_path)


Total unique matches where winner is null and batting team is India: 1205


match_id   season  start_date                                              venue  innings  ball batting_team  bowling_team       striker non_striker          bowler  runs_off_bat  extras  wides  noballs  byes  legbyes  penalty wicket_type player_dismissed other_wicket_type other_player_dismissed  wicket  striker balls faced  total striker runs  player out runs  player out balls faced  gender                             event  match_number   toss_winner toss_decision player_of_match       winner  winner_runs  winner_wickets outcome format  type        full name_striker country_striker batting style_striker   bowling style_striker playing role_striker                                major teams_striker                                  image url_striker         full name_bowler country_bowler batting style_bowler   bowling style_bowler playing role_bowler                                 major teams_bowler                                   image url_bowler player_of_match.1  \
486669    1157757  2018/19  2018-10-29                                  Brabourne Stadium        1   0.1        India   West Indies     RG Sharma    S Dhawan       KAJ Roach             4       0    NaN      NaN   NaN      NaN      NaN         NaN              NaN               NaN                    NaN       0                  1.0                 4.0              NaN                     NaN    male         West Indies tour of India           4.0         India           bat       RG Sharma        India        224.0             NaN     NaN    ODI  Intl    Rohit Gurunath Sharma           India        Right hand Bat      Right arm Offbreak     Top order Batter  India, Mumbai, Mumbai Indians, Air India, Decc...  https://img1.hscicdn.com/image/upload/f_auto,t...  Kemar Andre Jamal Roach    West Indies       Right hand Bat  Right arm Fast medium              Bowler  West Indies, Antigua Hawksbills, Barbados, Bri...  https://img1.hscicdn.com/image/upload/f_auto,t...               NaN   
2666167    565820     2012  2012-09-11                    MA Chidambaram Stadium, Chepauk        2   0.1        India   New Zealand     G Gambhir     V Kohli        KD Mills             1       0    NaN      NaN   NaN      NaN      NaN         NaN              NaN               NaN                    NaN       0                  1.0                 1.0              NaN                     NaN    male  New Zealand in India T20I Series           2.0         India         field     BB McCullum  New Zealand          1.0             NaN     NaN    T20  Intl           Gautam Gambhir           India         Left hand Bat                Legbreak     Top order Batter  India, Delhi, Delhi Daredevils, Essex, India C...  https://img1.hscicdn.com/image/upload/f_auto,t...         Kyle David Mills    New Zealand       Right hand Bat  Right arm Fast medium              Bowler  New Zealand, Auckland, Kings XI Punjab, Lincol...  https://img1.hscicdn.com/image/upload/f_auto,t...               NaN   
1118215    267708  2006/07  2007-01-27                    MA Chidambaram Stadium, Chepauk        1   0.1        India   West Indies    RV Uthappa   G Gambhir       JE Taylor             0       0    NaN      NaN   NaN      NaN      NaN         NaN              NaN               NaN                    NaN       0                  1.0                 0.0              NaN                     NaN    male   West Indies in India ODI Series           3.0   West Indies         field      MN Samuels  West Indies          NaN             3.0     NaN    ODI  Intl       Robin Venu Uthappa           India        Right hand Bat        Right arm Medium               Batter  India, Air India, Air India Red, Atlanta Rider...  https://img1.hscicdn.com/image/upload/f_auto,t...    Jerome Everton Taylor    West Indies       Right hand Bat         Right arm Fast              Bowler  West Indies, Jamaica, Jamaica Tallawahs, Kings...  https://img1.hscicdn.com/image/upload/f_auto,t...               NaN   
507090    1172161  2018/1

In [6]:
import pandas as pd

# Load the dataset
player_metadata_path = r"D:\commentary_matches\ball_by_ball_data.csv"
df_metadata = pd.read_csv(player_metadata_path)

# Filter rows where 'batting_team' is 'India'
#df_india_batting = df_metadata[df_metadata['bowling_team'] == 'India']
#df_india_batting = df_metadata[(df_metadata['format'] == 'ODI') & (df_metadata['batting_team'] == 'Australia') & (df_metadata['gender'] == 'male')]
df_india_batting = df_metadata[(df_metadata['bowling_team'] == 'India') & (df_metadata['gender'] == 'female')]


# Count unique match_id values
unique_match_count = df_india_batting['match_id'].nunique()

print("Total unique matches where batting team is India:", unique_match_count)

C:\Users\ariad\AppData\Local\Temp\ipykernel_18200\2515051777.py:5: DtypeWarning: Columns (1,20,21,36,53,54,55,56,57) have mixed types. Specify dtype option on import or set low_memory=False.
  df_metadata = pd.read_csv(player_metadata_path)


Total unique matches where batting team is India: 258
